In [2848]:
import re
from bs4 import BeautifulSoup
import requests
import html5lib
import json

In [2849]:
url = 'https://www.cna.com.tw/list/aspt.aspx'
res = requests.get(url)
soup = BeautifulSoup(res.text,'html5lib')

In [2850]:
n=0
labels=[]
#label_dic = {}
while n < len(soup.select_one('#pnProductNavContents > ul').findAll('li')):
    try :
        lab = soup.select_one('#pnProductNavContents > ul').findAll('li')[n].find('a',{'class':'first-level'}).text
        url =soup.select_one('#pnProductNavContents > ul').findAll('li')[n].find('a',{'class':'first-level'})['href']
    except:(TypeError,IndentationError)
    labels.append((url,lab))
    n += 1
labels = list(set(labels))
labels.remove(('http://cnavideo.cna.com.tw', '影音'))
labels.remove(('/list/aall.aspx', '即時'))
labels.append(('https://www.cna.com.tw/list/aall.aspx', '即時'))
#labels.remove(('https://www.cna.com.tw/keyword/九合一.aspx', '九合一'))
labels.remove(('https://www.cna.com.tw/list/sp.aspx', '專題'))
labels.remove(('https://www.cna.com.tw/list/aall.aspx', '即時'))

In [2851]:
labs = []
for item in labels:
    item = [item[0],item[1]]

    item[0] = re.search(r'list\/\w+',item[0]).group()[5:]
    labs.append(item)

In [2852]:
def payload(item):
    payload={
        'id': '1056893641102242',
    'ev': 'Microdata',
    'dl': item[0],
    'rl': 'https://www.cna.com.tw/',
    'if': 'false',
    'ts': '1541087113735',
    'cd[Schema.org]': [],
    #'cd[OpenGraph]': {"og:url":"https://www.cna.com.tw/list/ahel.aspx","og:title":"生活 | 中央社 CNA","og:description":"想知道統一發票、大樂透、威力彩開獎號碼、各種醫療保健、交通氣象、颱風動態等生活資訊，及升學考試、教育政策、課綱改革等文教訊息，通通都在中央社生活新聞。","og:image:height":"200","og:image:width":"200","og:image":"https://img5.cna.com.tw/www/images/pic_fb.jpg","og:type":"article","article:author":"https://www.facebook.com/cnanewstaiwan","article:publisher":"https://www.facebook.com/cnanewstaiwan"}
    #'cd[Meta]': {"title":"\n\t生活 | 中央社 CNA\n","meta:description":"想知道統一發票、大樂透、威力彩開獎號碼、各種醫療保健、交通氣象、颱風動態等生活資訊，及升學考試、教育政策、課綱改革等文教訊息，通通都在中央社生活新聞。","meta:keywords":"News, 新聞, 即時新聞, 中央社"}
    'cd[DataLayer]': [],
    'cd[JSON-LD]': [],
    'sw': '1280',
    'sh': '5000',#'720',
    'v': '2.8.30',
    'r': 'stable',
    'a': 'tmgoogletagmanager',
    'ec': '1',
    'o': '30',
    'fbp': 'fb.2.1541074934894.620990608',
    'it': '1541087112886',
    'coo': 'false',
    'es': 'automatic',
    }
    return payload

In [2853]:
labs_soup=[]
for item in labs:
    soups=[]
    n=1
    while n < 13:
        url = 'https://www.cna.com.tw/cna2018api/api/simplelist/categorycode/'+item[0]+'/pageidx/'+str(n)
        res = requests.get(url)
        soup = BeautifulSoup(res.text,'html5lib')
        body = soup.findAll('body')[0].getText()
        PageUrl = re.findall(r'\"PageUrl\"\:\S[^\,]+',body)
        urls = [txt[11:-1] for txt in PageUrl]
        soups.extend(urls)
        n += 1
        if len(urls) < 20:
            break
    labs_soup.append([soups,item[1]])

In [2854]:
news={}
newslist=[]
for lab in labs_soup:
    lab_name = lab[1]
    lab_urls = lab[0]
    n = 0
    for url in lab_urls:
        res = requests.get(url)
        soup = BeautifulSoup(res.text,'html5lib')
        txt = ""
        try:
            title = soup.find_all('div',{'class':'centralContent'})[0].find_all('h1')[0].getText()
            for s in soup.find_all('div',{'class':'paragraph'})[0].findAll('p'):
                txt=txt+s.getText()
        except:IndexError
        research = re.search(r'[\）\)\：\:\》](.+[\。\!\?\s])+',txt)
        if research == None or len(research.group())<2:
            print(txt)
        else:
            txt = re.search(r'[\）\)\：\:\》](.+[\。\!\?\s])+',txt).group()[1:]

        page = [[title,txt],lab_name]
        newslist.append(page)
        news[txt]=lab_name
        n += 1
        if n % 20 == 0:
            print((lab_name,n),end=",")


('科技', 20),('科技', 40),('科技', 60),('科技', 80),('科技', 100),('地方', 20),('地方', 40),('地方', 60),('地方', 80),('地方', 100),('社會', 20),('社會', 40),('社會', 60),('社會', 80),('社會', 100),('運動', 20),('運動', 40),('運動', 60),('運動', 80),('運動', 100),('兩岸', 20),('兩岸', 40),('兩岸', 60),('兩岸', 80),中央社駐香港特派員張謙/12月3日4年前「占中運動」爆發時，香港泛民主派一度氣勢如虹，並於2016年底的立法會選舉取得不錯成績，但近年來形勢逆轉，泛民面對不少內憂壓力。挾著年輕力量的崛起，泛民於2016年9月的立法會選舉大有斬獲，共取得26席。當中包括一人一票的分區直選議席，以及以業界區分的功能組別議席。功能組別以業界人士或代表區分，從來都是泛民較弱的版塊，但當年泛民在這方面獲得的選票大增，顯示其勢力正往業界延伸，威脅親政府建制派的基本盤。但「占中」之後，當局在北京中央高喊必須對「港獨」零容忍的情況下，開始以行政手段限制立場較為偏激的泛民人士參選。主要要求各候選人在參選前，必須簽署一份參選聲明，表明自己擁護基本法和保證效忠香港特別行政區。這項新規定導致一些泛民代表、特別是主張「港獨」的年輕代表，無法參加當年的立法會選舉，甚至讓新成立的年輕政黨香港眾志，一夜之間被排除在選舉之外，無法透過參選而進入香港管治架構。選後，當局也對泛民當選者窮追猛打，以他們在宣誓就任時未符合基本法所規定的「莊嚴」要求，向法院提出聲請，要求褫奪他們的資格，結果導致泛民6人喪失議席。進入2018年，泛民的困境並未消除。在立法會議員補選中未能拿回失去的全部議席，僅取回3席，失去另外2席，讓泛民在議會的人數減少。今年3月和11月，當局為泛民失去的其中5個議席進行補選，其中3月補選4人，11月補選1人。結果泛民在3月只贏回兩席，失去另外2席。更重要的是，泛民在一人一票的地方直選，被建制派打敗而失去1席，這是泛民和建制派歷來在一對一的對決下，首次落敗。在上月的補選中，泛民同樣在地方直選中落敗，受挫的的更是泛民元老級人馬、工黨成員李卓人。對於泛民連續兩次在一人一票地方直選、一對一

In [2855]:
newslist[1]

[['NASA洞察號探測器捕捉成功 人類首度聽見火星風聲',
  '美國國家航空暨太空總署（NASA）今天表示，火星探測器「洞察號」（InSight）捕捉到火星的風所造成的振動後，人類首次聽見這顆紅色星球的低沉風聲，予人強烈的感受。法新社報導，風速介於每秒5至7公尺的和風，吹過洞察號太陽能板，所造成的振動被捕捉下來。「洞察號」無人探測器11月26日降落在遍布塵土且荒涼的地球鄰居火星。收錄振動的是「洞察號」探測器內部的氣壓計和艙面地震儀等兩個感應器。「洞察號」的機械手臂未來將會把地震儀部署在火星地表。倫敦帝國學院（Imperial College London）首席研究員派克（Thomas Pike）在電話記者會上表示：「這是地震儀收集的最初15分鐘資料」。他補充說道，「有點像風中飄揚的旗子」。「聽起來真的有如超脫塵世，也是確實如此。」NASA噴射推進實驗室（Jet Propulsion Laboratory）的「洞察號」首席研究員班納特（Bruce Banerdt）說，捕捉到大約下午5時從西北吹向東南的這道風，可說是「喜出望外」。'],
 '科技']

In [2856]:
import jieba
import nltk

In [2857]:
stopwords=[]
with open('stopwords_ch.txt', 'r', encoding='UTF-8') as file:
    for data in file.readlines():
        data = data.strip()
        stopwords.append(data)

In [2858]:
filterwords=[
    '年','月','中央社','記者','編輯','譯者','日電',
    '\n',' ','「','」'
    ,'今天','說','表示','年','月','日','後','前','時','應','中','今年'
    ,'兩','下','人','最','次','再','先','盡量'
]

In [2859]:
articles = []
titles = []
for news in newslist:
    articles.append((news[0][1],news[1]))
    titles.append((news[0][0],news[1]))


In [2860]:
books = []

n = 0
while n < len(titles):
    head_dic = {}
    txt_dic = {}
    head = titles[n]
    txt = articles[n]
    
    head_dic[head[0]] = head[1]
    txt_dic[txt[0]] = txt[1]
    books.append([head_dic,txt_dic])
    n += 1

In [2861]:
# book = [ head_dic , txt_dic ]
books[1]

[{'NASA洞察號探測器捕捉成功 人類首度聽見火星風聲': '科技'},
 {'美國國家航空暨太空總署（NASA）今天表示，火星探測器「洞察號」（InSight）捕捉到火星的風所造成的振動後，人類首次聽見這顆紅色星球的低沉風聲，予人強烈的感受。法新社報導，風速介於每秒5至7公尺的和風，吹過洞察號太陽能板，所造成的振動被捕捉下來。「洞察號」無人探測器11月26日降落在遍布塵土且荒涼的地球鄰居火星。收錄振動的是「洞察號」探測器內部的氣壓計和艙面地震儀等兩個感應器。「洞察號」的機械手臂未來將會把地震儀部署在火星地表。倫敦帝國學院（Imperial College London）首席研究員派克（Thomas Pike）在電話記者會上表示：「這是地震儀收集的最初15分鐘資料」。他補充說道，「有點像風中飄揚的旗子」。「聽起來真的有如超脫塵世，也是確實如此。」NASA噴射推進實驗室（Jet Propulsion Laboratory）的「洞察號」首席研究員班納特（Bruce Banerdt）說，捕捉到大約下午5時從西北吹向東南的這道風，可說是「喜出望外」。': '科技'}]

In [2862]:
def get_tags(books=books):

    prelab = ''
    tags = {}
    for book in books:
        head_dic = book[0]
        txt_dic = book[1]
        n=0
        for dic in [head_dic,txt_dic]:

            for lab in ['生活','運動','政治','科技','國際','兩岸','產經','社會','地方','娛樂','證券','文化']:
                if list(dic.values())[0]==lab:
                    if prelab != lab:
                        txt=''
                    txt += list(dic.keys())[0]
                    tags[list(dic.values())[0]] = txt
                    prelab = lab
            if n == 0:
                title_tags = tags
            elif n == 1:
                txt_tags = tags
            n += 1
    return title_tags,txt_tags

In [2863]:
title_tags,txt_tags = get_tags(books)

In [2864]:
title_tags

{'兩岸': '行動支付太強勢 陸整頓商家拒收現金中國行動支付普遍，卻衍生商家拒收現金的亂象，引發民眾抱怨。經官方要求整改後，5個月內已處理602起案例。像是阿里巴巴旗下的超市原本只能用app結帳，現在也設立現金收銀櫃檯。越來越多只透過手機行動支付收款的商家，讓中國人民銀行在7月12日不得不發出公告，強調人民幣是法定貨幣，任何單位和個人不得以格式條款、通知、聲明、告示等方式拒收現金。公告發布後，人行展開整治工作。根據陸媒經濟日報今天報導，至今全國共處理拒收現金行為602起，已有558起整改到位。標榜線上和線下融合的「新零售」範例、阿里巴巴旗下的連鎖超市「盒馬鮮生」，原本只採會員制，且規定結帳只能用手機app，造成一些非會員或上了年紀的消費者不滿。在收到投訴後，盒馬鮮生成了上海人行總部優先要求整改的對象。經過整治，這家超市的每間門市都設有現金收銀通道，且標識明顯。中國人民大學重陽金融研究院高級研究員董希淼表示，拒收現金既損害了人民幣的法定地位，也損害了消費者對支付方式的選擇權，更不利於形成公平競爭的市場環境。報導說，「拒收現金違法」的觀念已經深入人心。台灣腔vs上海腔  台旅會推台灣週末遊今天開始，上海30個地鐵站內將同步播放台灣旅遊宣傳片，片中穿插「台灣腔」與「上海腔」，希望吸引上海旅客到台灣過冬，體驗跨年、享受溫泉、品味小鎮。上海話拿「有腔調」一詞來形容人或事物有格調、有品味。台灣海峽兩岸觀光旅遊協會（台旅會）今天發布一支最新台灣旅遊宣傳影片「臺灣（腔）有腔調」，就是取「有腔調」的雙關涵義。交通部觀光局長、台旅會會長周永暉說，目前大陸開放47個來台自由行城市中，以上海直飛台灣的航班最為密集，每週高達100多班次，上海的旅客隨時可以輕鬆到台灣度個週末。希望透過宣傳片，提醒上海民眾在選擇旅遊目的地時，別忘了距離最近、體驗最豐富的台灣。台旅會上海辦事處主任蘇宇宏表示，影片角色涵蓋台灣各行各業，象徵來台旅遊的食住行和文化，透過他們的「台灣腔」強化全片的記憶點，表達台灣人的熱情好客，與台灣的好吃、好玩、好看和最難能可貴的人情味。這支宣傳片充滿趣味，片中，士林夜市的蚵仔煎小吃攤老闆一句「超好吃的哦」，緊接著是畫外音「米道老靈額」，在上海話是味道很好的意思；墾丁海邊無敵海景的民宿裡，民宿老闆娘問客人「住在海邊是不是有夠讚」，上海旅客回應一句「交關好」，形成兩個城市有趣的對話。蘇

In [2865]:
txt_tags

{'兩岸': '行動支付太強勢 陸整頓商家拒收現金中國行動支付普遍，卻衍生商家拒收現金的亂象，引發民眾抱怨。經官方要求整改後，5個月內已處理602起案例。像是阿里巴巴旗下的超市原本只能用app結帳，現在也設立現金收銀櫃檯。越來越多只透過手機行動支付收款的商家，讓中國人民銀行在7月12日不得不發出公告，強調人民幣是法定貨幣，任何單位和個人不得以格式條款、通知、聲明、告示等方式拒收現金。公告發布後，人行展開整治工作。根據陸媒經濟日報今天報導，至今全國共處理拒收現金行為602起，已有558起整改到位。標榜線上和線下融合的「新零售」範例、阿里巴巴旗下的連鎖超市「盒馬鮮生」，原本只採會員制，且規定結帳只能用手機app，造成一些非會員或上了年紀的消費者不滿。在收到投訴後，盒馬鮮生成了上海人行總部優先要求整改的對象。經過整治，這家超市的每間門市都設有現金收銀通道，且標識明顯。中國人民大學重陽金融研究院高級研究員董希淼表示，拒收現金既損害了人民幣的法定地位，也損害了消費者對支付方式的選擇權，更不利於形成公平競爭的市場環境。報導說，「拒收現金違法」的觀念已經深入人心。台灣腔vs上海腔  台旅會推台灣週末遊今天開始，上海30個地鐵站內將同步播放台灣旅遊宣傳片，片中穿插「台灣腔」與「上海腔」，希望吸引上海旅客到台灣過冬，體驗跨年、享受溫泉、品味小鎮。上海話拿「有腔調」一詞來形容人或事物有格調、有品味。台灣海峽兩岸觀光旅遊協會（台旅會）今天發布一支最新台灣旅遊宣傳影片「臺灣（腔）有腔調」，就是取「有腔調」的雙關涵義。交通部觀光局長、台旅會會長周永暉說，目前大陸開放47個來台自由行城市中，以上海直飛台灣的航班最為密集，每週高達100多班次，上海的旅客隨時可以輕鬆到台灣度個週末。希望透過宣傳片，提醒上海民眾在選擇旅遊目的地時，別忘了距離最近、體驗最豐富的台灣。台旅會上海辦事處主任蘇宇宏表示，影片角色涵蓋台灣各行各業，象徵來台旅遊的食住行和文化，透過他們的「台灣腔」強化全片的記憶點，表達台灣人的熱情好客，與台灣的好吃、好玩、好看和最難能可貴的人情味。這支宣傳片充滿趣味，片中，士林夜市的蚵仔煎小吃攤老闆一句「超好吃的哦」，緊接著是畫外音「米道老靈額」，在上海話是味道很好的意思；墾丁海邊無敵海景的民宿裡，民宿老闆娘問客人「住在海邊是不是有夠讚」，上海旅客回應一句「交關好」，形成兩個城市有趣的對話。蘇

In [2866]:
def get_fwords(tags={},top=300):


    lab_fwords={}
    lab_Ftwowords = {}
    for labname in tags.keys():
        print(labname,end=',')
        lab_words = tags[labname]
    #    seg_list = jieba.cut_for_search(lab_words)#, cut_all=False)
        seg_list = jieba.cut(lab_words, cut_all=False)
        txt = ",".join(seg_list)
        tokens = txt.split(',')
        tokens = list(filter(lambda a: a not in stopwords and a not in filterwords and a.isalpha() == True,tokens))#and len(a)>1, tokens))
        ###
        lab_alltwowords = list(nltk.bigrams(tokens))
        two = nltk.FreqDist(lab_alltwowords).most_common(top)
        lab_Ftwowords[labname] = [i[0]+i[1] for i,j in two]
        ###
        lab_fwords[labname] =  [i[0] for i in nltk.FreqDist(tokens).most_common(top)]
    return lab_fwords,lab_Ftwowords

In [2867]:
txt_fwords,txt_Ftwowords = get_fwords(txt_tags)

科技,地方,社會,運動,兩岸,證券,生活,娛樂,國際,產經,政治,文化,

In [2868]:
txt_fwords2 = get_fwords(txt_tags)[0]

科技,地方,社會,運動,兩岸,證券,生活,娛樂,國際,產經,政治,文化,

In [2869]:
title_fwords['國際']

['北韓',
 '脫歐',
 '梅伊',
 '任正',
 '背心',
 'PEI',
 '抗議',
 '梅克爾',
 '情報',
 '總理',
 '華府',
 '美軍',
 '聯合國',
 '條約',
 '金正恩',
 '禁令',
 '半島',
 '燃油稅',
 '克朗',
 '普',
 '凱倫',
 '鮑爾',
 '白宮',
 '恐怖',
 '黨魁',
 '回訪',
 '調漲',
 '舟是',
 '表決',
 '直接',
 '基民黨',
 '麥茲',
 '反',
 '軍事',
 '暴力',
 '首晟',
 '玩具',
 '保釋',
 '本案',
 '民主黨',
 '杜魯道',
 '攻擊',
 '細節',
 '轉機',
 '軍方',
 '阿瑪',
 '葉門',
 '福島',
 '外國',
 '大使',
 '會長',
 '清秀',
 '佳人',
 '旅遊業',
 '空中',
 'F',
 '海軍',
 '技能',
 '走廊',
 'し',
 '謝長廷',
 '間諜',
 '知情',
 'CNN',
 '法新社',
 '李勇',
 '參議院',
 '菲律賓',
 '首相',
 'て',
 '為由',
 '現年',
 '司法部',
 '解放軍',
 '紹吉',
 '耿爽',
 '留台',
 '島',
 '柬埔寨',
 '平壤',
 '願',
 '危機',
 '首爾',
 '咖啡館',
 '斯特',
 '陸戰隊',
 '支持度',
 '明均',
 '戒嚴',
 '下令',
 '工廠',
 '俠客島',
 '烏克蘭',
 '迪',
 '叛軍',
 '解除',
 '作出',
 '報復',
 '駐日',
 '河野',
 'WTO',
 '利益',
 '諾爾特',
 '敘利亞',
 '獲釋',
 '會談',
 '國集團',
 '警告',
 '眾議院',
 '亞桑傑',
 '領導人',
 '此舉',
 '群眾',
 '艾里',
 '賽宮',
 '武器',
 '週末',
 '殲',
 '在寅',
 '黎巴嫩',
 '延長',
 '民答那峨島',
 '聽證會',
 '波音',
 '推文',
 '東廂',
 '崔大偉',
 'の',
 'を',
 '孕母',
 '巴布亞',
 '受審',
 '密切',
 '干預',
 '校友會',
 '台印',
 '修改',
 '不久',
 '評價',
 

In [2870]:
#type(get_fwords(title_tags))

In [2871]:
#去除交集的高頻字
def remove_mix(t):
    lab_fwords = t[0]
    lab_Ftwowords = t[1]


    dic3={}
    for lab in lab_fwords.keys():   
        word_content2 = lab_fwords[lab].copy()
        for lab2 in lab_fwords.keys():        
            if lab != lab2:
                word_content = [w for w in lab_fwords[lab] if (w in [a for a in lab_fwords[lab2]])]
                for w in word_content:
                    try:
                        word_content2.remove(w)                  
                    except ValueError:
                        pass
        dic3[lab] = word_content2  



    dic2={}
    for lab in lab_Ftwowords.keys():   
        word_content2 = lab_Ftwowords[lab].copy()
        for lab2 in lab_Ftwowords.keys():        
            if lab != lab2:
                word_content = [w for w in lab_Ftwowords[lab] if (w in [a for a in lab_Ftwowords[lab2]])]
                for w in word_content:
                    try:
                        word_content2.remove(w)                   
                    except ValueError:
                        pass
        dic2[lab] = word_content2
        
    return dic3,dic2

In [2872]:
title_fwords,title_Ftwowords = remove_mix(get_fwords(title_tags,700))
txt_fwords,txt_Ftwowords = remove_mix(get_fwords(txt_tags,800))

科技,地方,社會,運動,兩岸,證券,生活,娛樂,國際,產經,政治,文化,科技,地方,社會,運動,兩岸,證券,生活,娛樂,國際,產經,政治,文化,

In [2873]:
'陳菊' in txt_fwords['文化']

False

In [2874]:
[i for i in txt_fwords['政治'] if i in txt_fwords['文化']]

[]

In [2875]:
def get_allFtwowords(lab_Ftwowords={}):
    
    
    All_Ftwowords2=[]
    for n in lab_Ftwowords.values():
        for m in n:
            All_Ftwowords2.append(m)

    All_Ftwowords = []
    for w in All_Ftwowords2:
        All_Ftwowords.append(w)
    return All_Ftwowords

In [2876]:
title_allFtwo = get_allFtwowords(title_Ftwowords)
txt_allFtwo = get_allFtwowords(txt_Ftwowords)

In [2877]:
txt_allFtwo

['太空總署',
 '美國國家',
 '國家航空',
 '航空暨',
 '暨太空',
 '總署NASA',
 '報導蘋果',
 '無線通訊',
 '身分識別',
 '研究團隊',
 '指紋辨識',
 'AppleWatch',
 '運載火箭',
 '國際太空站',
 '發射升空',
 '邱培鈺',
 '加密貨幣',
 '月球背面',
 '用戶資料',
 '漢諾威電腦展',
 '登陸火星',
 '火星探測',
 '嫦娥四號',
 'Google翻譯',
 '臉部辨識',
 '熱門話題',
 '逐字稿',
 '螢幕指紋',
 '國外科技',
 '科技網站',
 '聯合號火箭',
 '研究人員',
 '太空葬',
 '離子風',
 'GSLVMk',
 'MkIII',
 '噴射推進',
 '推進實驗室',
 '應用程式',
 '先前報導',
 '小行星',
 'TWID身分',
 '萬公里',
 '降落火星',
 '台法科技獎',
 '董明珠',
 '火星探測器',
 '探測器洞察號',
 '洞察號InSight',
 '成功發射',
 '探測任務',
 '電子郵件',
 '外媒報導',
 '新款iPhone',
 '加拉巴戈',
 '巴戈斯',
 '樂土太空',
 '歐塞瑞斯',
 '法國國家',
 '識別服務',
 '航太總署',
 '微創手術',
 '通訊晶片',
 '版iPhone',
 '機械手臂',
 '雅婷逐字',
 '台灣人工',
 '美國太空',
 '送入太空',
 '軌道衛星',
 '俄羅斯聯合號',
 '瑞斯號',
 '科學研究',
 '約公里',
 '翻譯網頁',
 '光達技術',
 '蘋果深耕',
 '太空軌道',
 '發射羅老',
 '羅老號',
 '識別中心',
 '研究成果',
 '成果發表',
 '海達路德',
 '火星表面',
 '火星地震',
 '比特幣價格',
 '火星大氣層',
 '訓練中心',
 '蘋果積極',
 '電子元件',
 '北斗三號',
 '發射任務',
 'AI領域',
 '超級電腦',
 '台灣杉二號',
 '部長陳良基',
 '語音新聞',
 '無法使用',
 '透過手機',
 '顯示臉書',
 '重要里程碑',
 '智慧AI',
 '重達公斤',
 '年度熱門',
 '網站Patently',
 'Paten

In [2878]:
import random
random.shuffle(books)

In [2879]:
def pos_title_features(article,top):
    features={}
    t = ''
    seg_list = jieba.cut_for_search(article)#, cut_all=False)
    t = ",".join(seg_list)
    article_tokens = t.split(',')
    article_tokens = [w for w in article_tokens if w.isalpha()]

    filt_tokens = list(filter(lambda a: a not in stopwords and a not in filterwords , article_tokens))#and len(a)>1, article_tokens))
    ###
    twowords = list(nltk.bigrams(article_tokens))
#    two = nltk.FreqDist(twowords).most_common(int(top*2/3))

    alltwowords2 = [i[0]+i[1] for i in twowords]
#    print(alltwowords2)
    intwowords = [two for two in alltwowords2 if two in title_allFtwo]
#    print(intwowords)
    ftwowords = nltk.FreqDist(intwowords).most_common(int(top*2/3))
    toks = [w[0] for w in nltk.FreqDist(filt_tokens).most_common(top)]
#    print(ftwowords)
#    print(([i[0] for i in ftwowords] ))
    if len([i[0] for i in ftwowords if i[0] in [w for li in title_Ftwowords.values() for w in li]])==0 and len([i for i in toks if i in [w for li in title_fwords.values() for w in li]])==0:
        for i in ftwowords:
            w = i[0]
            features[w] = True
            print(w+'1')
            
    else:
        for i in ftwowords:
            w = i[0]
            if w in [w for li in title_Ftwowords.values() for w in li]:
                features[w] = True
#                print(w+'2')

#        print(w+'2')
    ###
    
#    print(toks)
#    print([w for li in title_fwords.values() for w in li])
    if len([i for i in toks if i in [w for li in title_fwords.values() for w in li]])==0 and len([i[0] for i in ftwowords if i[0] in [w for li in title_Ftwowords.values() for w in li]])==0:
        for i in toks:
            #features[i] = True
            print(i+'3')
    else:
#        for tok in toks:
#            print(tok+'3')
        bigcontent=[]
        kk=''
        for k in title_fwords.keys():
            content=[]
            for tok in toks:

    #                print([w for li in txt_fwords[k] for w in li])
                if tok in title_fwords[k] :

##                    print(tok+'1'+k)
                    content.append(tok)
                if len(bigcontent) < len(content):
                    bigcontent = content.copy()
                    kk = k
##            print(len(bigcontent))
        for tok in bigcontent:  
#                print(tok+','+kk)
            features[tok] = True
    #                print(tok+'4')
    #        print(tok+'1')
    return features

In [2880]:
pos_title_features(test_title,200)

{'助': True}

In [2881]:
def get_title_featuresets(book,top=200):
    n = 0
#    featuresets=[]
#    for book in books:
    head_dic = book[0]
#        features = {}
    article = list(head_dic.keys())[0]
    labname = list(head_dic.values())[0]
    features = pos_title_features(article,top)

    if len(list(features.keys())) < 2:
        #feature_item = [features,labname]
        feature_item = [{},labname]
    else:
        feature_item = [features,labname]
#        featuresets.append(feature_item)
    n += 1
    if n % 20 == 0:
        print(n,end=',')

#    return featuresets
    return feature_item

In [2882]:
def pos_txt_features0(article,top):
    features={}
    t = ''
    seg_list = jieba.cut_for_search(article)#, cut_all=False)
    t = ",".join(seg_list)
    article_tokens = t.split(',')
    article_tokens = [w for w in article_tokens if w.isalpha()]

    filt_tokens = list(filter(lambda a: a not in stopwords and a not in filterwords , article_tokens))#and len(a)>1, article_tokens))
    ###
    twowords = list(nltk.bigrams(article_tokens))
#    two = nltk.FreqDist(twowords).most_common(int(top*2/3))

    alltwowords2 = [i[0]+i[1] for i in twowords]
#    print(alltwowords2)
    intwowords = [two for two in alltwowords2 if two in txt_allFtwo]
#    print(intwowords)
    ftwowords = nltk.FreqDist(intwowords).most_common(int(top*2/3))
    toks = [w[0] for w in nltk.FreqDist(filt_tokens).most_common(top)]
#    print(ftwowords)
#    print(([i[0] for i in ftwowords] ))
    if len([i[0] for i in ftwowords if i[0] in [w for li in txt_Ftwowords.values() for w in li]])==0 and len([i for i in toks if i in [w for li in title_fwords.values() for w in li]])==0:
        for i in ftwowords:
            w = i[0]
            features[w] = True
            print(w+'1')
            
    else:
        for i in ftwowords:
            w = i[0]
            if w in [w for li in txt_Ftwowords.values() for w in li]:
                features[w] = True
#                print(w+'2')

#        print(w+'2')
    ###
    
#    print(toks)
#    print([w for li in title_fwords.values() for w in li])
    if len([i for i in toks if i in [w for li in txt_fwords.values() for w in li]])==0 and len([i[0] for i in ftwowords if i[0] in [w for li in title_Ftwowords.values() for w in li]])==0:
        for i in toks[:int(len(toks)*0.25)]:
            features[i] = True
            print(i+'3')
    else:
        for tok in toks:
            if tok in [w for li in txt_fwords.values() for w in li]:
                features[tok] = True
#                print(tok+'4')
#        print(tok+'1')
    return features

In [2883]:
def pos_txt_features(article,top):
    features={}
    t = ''
    seg_list = jieba.cut_for_search(article)#, cut_all=False)
    t = ",".join(seg_list)
    article_tokens = t.split(',')
    article_tokens = [w for w in article_tokens if w.isalpha()]

    filt_tokens = list(filter(lambda a: a not in stopwords and a not in filterwords , article_tokens))#and len(a)>1, article_tokens))
    ###
    twowords = list(nltk.bigrams(article_tokens))
#    two = nltk.FreqDist(twowords).most_common(int(top*2/3))

    alltwowords2 = [i[0]+i[1] for i in twowords]
#    print(alltwowords2)
    intwowords = [two for two in alltwowords2 if two in txt_allFtwo]
#    print(intwowords)
    ftwowords = nltk.FreqDist(intwowords).most_common(int(top))
    toks = [w[0] for w in nltk.FreqDist(filt_tokens).most_common(top)]
#    print(ftwowords)
#    print(([i[0] for i in ftwowords] ))

    if len([i for i in toks if i in [w for li in txt_fwords.values() for w in li]])==0 and len([i[0] for i in ftwowords if i[0] in [w for li in txt_Ftwowords.values() for w in li]])==0:
        for i in toks[:int(len(toks)*0.25)]:
            features[i] = True
#            print(i+'3')
    else:
#        for tok in toks:
#            print(tok+'3')
        bigcontent=[]
        kk=''
        for k in txt_fwords.keys():
            content=[]
            for tok in toks:

    #                print([w for li in txt_fwords[k] for w in li])
                if tok in txt_fwords[k] :

                    print(tok+'1'+k)
                    content.append(tok)
                if len(bigcontent) < len(content):
                    bigcontent = content.copy()
                    kk = k

##           print(len(bigcontent))
        for tok in bigcontent:  
            print(tok+','+kk)
            features[tok] = True
    #                print(tok+'4')
    #        print(tok+'1')
    if len([i[0] for i in ftwowords if i[0] in [w for li in txt_Ftwowords.values() for w in li]])==0 and len([i for i in toks if i in [w for li in txt_fwords.values() for w in li]])==0:
        for i in ftwowords[:int(len(ftwowords)*0.25)]:
            w = i[0]
            features[w] = True
            print(w+'1')
            
    else:
#        for tok in toks:
#            print(tok+'3')
        bigcontent=[]
        kk2=''
        for k in txt_Ftwowords.keys():
            content=[]
            for i in ftwowords:
                tok = i[0]
    #                print([w for li in txt_Ftwowords[k] for w in li])
                if tok in txt_Ftwowords[kk] :

                    print(tok+'1'+k)
                    content.append(tok)
                if len(bigcontent) < len(content):
                    bigcontent = content.copy()
#                    kk = k
##            print(len(bigcontent))
            for tok in bigcontent:  
#                print(tok+','+kk)
                features[tok] = True

#        print(w+'2')
    ###
    
#    print(toks)
#    print([w for li in title_fwords.values() for w in li])
    return features

In [2884]:
def get_txt_Flab0(article,top,get=5):
    features={}
    t = ''
    seg_list = jieba.cut_for_search(article)#, cut_all=False)
    t = ",".join(seg_list)
    article_tokens = t.split(',')
    article_tokens = [w for w in article_tokens if w.isalpha()]

    filt_tokens = list(filter(lambda a: a not in stopwords and a not in filterwords , article_tokens))#and len(a)>1, article_tokens))
    ###
    twowords = list(nltk.bigrams(article_tokens))
#    two = nltk.FreqDist(twowords).most_common(int(top*2/3))

    alltwowords2 = [i[0]+i[1] for i in twowords]
#    print(alltwowords2)
    intwowords = [two for two in alltwowords2 if two in txt_allFtwo]
#    print(intwowords)
    ftwowords = nltk.FreqDist(intwowords).most_common(int(top))
    toks = [w[0] for w in nltk.FreqDist(filt_tokens).most_common(top)]
#    print(ftwowords)
#    print(([i[0] for i in ftwowords] ))

    if len([i for i in toks if i in [w for li in txt_fwords.values() for w in li]])==0 and len([i[0] for i in ftwowords if i[0] in [w for li in txt_Ftwowords.values() for w in li]])==0:
        for i in toks[:int(len(toks)*0.25)]:
            features[i] = True
#            print(i+'3')
    else:
#        for tok in toks:
#            print(tok+'3')
        bigcontent=[]
        kk=''
        for k in txt_fwords.keys():
            content=[]
            for tok in toks:

    #                print([w for li in txt_fwords[k] for w in li])
                if tok in txt_fwords[k] :

 #                   print(tok+'1'+k)
                    content.append(tok)
                if len(bigcontent) < len(content):
                    bigcontent = content.copy()
                    kk = k
##           print(len(bigcontent))
        for tok in bigcontent[:get]:  
##                print(tok+','+kk)
            features[tok] = kk
            print(tok+'4')
    #        print(tok+'1')
    
    if len([i[0] for i in ftwowords if i[0] in [w for li in txt_Ftwowords.values() for w in li]])==0 and len([i for i in toks if i in [w for li in txt_fwords.values() for w in li]])==0:
        print(4)
        for i in ftwowords[:int(len(ftwowords)*0.25)]:
            w = i[0]
            features[w] = True
            print(w+'1')
            
    else:
#        for tok in toks:
        print('3')
        bigcontent2=[]
        kk2=''
        for k in txt_Ftwowords.keys():
            content2=[]
            for i in ftwowords:
                tok = i[0]
    #                print([w for li in txt_Ftwowords[k] for w in li])
                if tok in txt_Ftwowords[kk] :

#                    print(tok+'1'+k)
                    content2.append(tok)
                if len(bigcontent2) < len(content2):
                    bigcontent2 = content2.copy()
                    kk2 = kk
##            print(len(bigcontent))
            for tok in bigcontent2[:get]:  
 #               print(tok+'3'+kk2)
                features[tok] = kk2

#        print(w+'2')
    ###
    
#    print(toks)
#    print([w for li in title_fwords.values() for w in li])
    return features

In [2885]:
from collections import Counter
def get_top(article,top,get=5):
    features={}
    t = ''
    seg_list = jieba.cut_for_search(article)#, cut_all=False)
    t = ",".join(seg_list)
    article_tokens = t.split(',')
    article_tokens = [w for w in article_tokens if w.isalpha()]

    filt_tokens = list(filter(lambda a: a not in stopwords and a not in filterwords , article_tokens))#and len(a)>1, article_tokens))
    ###
    twowords = list(nltk.bigrams(article_tokens))
#    two = nltk.FreqDist(twowords).most_common(int(top*2/3))

    alltwowords2 = [i[0]+i[1] for i in twowords]
#    print(alltwowords2)
    intwowords = [two for two in alltwowords2 if two in txt_allFtwo]
#    print(intwowords)
    ftwowords = nltk.FreqDist(intwowords).most_common(int(top))
    toks = [w for w in nltk.FreqDist(filt_tokens).most_common(top)]
#    print(toks)
    selectwords = ([t for t in toks if t[0] in [w for li in txt_fwords.values() for w in li]])
    klist=[]
    for w in selectwords[:get]:
       
        for k in txt_fwords.keys():

            if w[0] in [s for s in txt_fwords[k]] :
                klist.append(k)
                print(w,k)
                features['top'] = Counter(klist).most_common(1)[0][0]



    return features

In [2886]:
get_top(test_txt,200,5)

('刺激', 6) 國際
('食品', 4) 政治
('日方', 3) 政治
('少數', 2) 兩岸
('國人', 2) 政治


{'top': '政治'}

In [2887]:
[s for li in txt_fwords.values() for s in li]

['火星',
 '太空',
 '火箭',
 '衛星',
 '發射',
 '洞察號',
 '地球',
 '任務',
 '用戶',
 'NASA',
 '總署',
 'AI',
 '降落',
 '升空',
 '辨識',
 '月球',
 '探測器',
 '科學家',
 '科技部',
 'Facebook',
 '飛行',
 '太空人',
 '探測',
 '識別',
 '登陸',
 '人類',
 'App',
 '無線',
 '飛機',
 '生物',
 'Apple',
 '螢幕',
 '機器人',
 '比特幣',
 'Google',
 '氣味',
 '太空船',
 '行星',
 '好奇號',
 '實驗室',
 '軟銀',
 '指紋',
 '外媒',
 '氣體',
 '搭載',
 '太空站',
 '貨幣',
 '陳良基',
 '當機',
 'ISRO',
 '基因',
 '電競',
 'Instagram',
 '象龜',
 '大小',
 '奈米',
 'Oath',
 '運載',
 '谷歌',
 '研究所',
 '漢諾威',
 '邱',
 '台法',
 '離子',
 '語音',
 '程式',
 '失敗',
 '公斤',
 '追蹤',
 '諾',
 '速度',
 '聯合號',
 '加州',
 '太陽系',
 '航太',
 '分子',
 '加密',
 '電腦展',
 '引擎',
 '資訊月',
 '巴西',
 'Watch',
 '材料',
 '嫦娥',
 '著陸',
 '星',
 '位於',
 '採用',
 '葬',
 '骨灰',
 '大氣層',
 '貝努',
 '實驗',
 '光達',
 '表面',
 '動力',
 '地質',
 '培鈺',
 '莫內',
 '車流',
 'InSight',
 '背面',
 '三號',
 '觀測',
 '用來',
 'SpaceX',
 '祖克柏',
 'Telstra',
 '重',
 'Space',
 '工程師',
 '試射',
 '網頁',
 '名為',
 '虛擬',
 '郵輪',
 '明珠',
 'Fitbit',
 '珊瑚',
 '英特爾',
 '研究員',
 '四號',
 '臉部',
 '愛立信',
 '逐字',
 '稿',
 '通信',
 '發動機',
 '商業化',
 'GSAT',
 'Tumblr',
 '瑞斯',

In [2888]:
txt_fwords.keys()

dict_keys(['科技', '地方', '社會', '運動', '兩岸', '證券', '生活', '娛樂', '國際', '產經', '政治', '文化'])

In [2889]:
def get_txt_featuresets(book,top=200):
    n = 0
#    featuresets=[]
#    for book in books:
    txt_dic = book[1]
#        features = {}
    article = list(txt_dic.keys())[0]
    labname = list(txt_dic.values())[0]
    features = pos_txt_features(article,top)
    feature_item = [features,labname]
#    featuresets.append(feature_item)
    n += 1
    if n % 20 == 0:
        print(n,end=',')

#    return featuresets
    return feature_item

In [2890]:
test_title="""
NBA／厄文爆發布朗覺醒 綠衫軍主場大勝尼克取4連勝

"""

test_txt="""
取得3連勝的波士頓塞爾提克今(7)日在主場迎戰紐約尼克，靠著「Uncle Drew」Kyrie Irving(厄文)在第3節大爆發、全場砍下22分，以及Jaylen Brown(布朗)「復活」以替補身分得到21分，塞爾提克終場以128:100擊敗對手，喜迎4連勝。

 

在開季不穩的狀況之後，綠衫軍近期慢慢步上正軌，連勝鵜鶘、騎士、灰狼3支隊伍，目前處於3連勝的高昂士氣當中。今天面對近年的弱隊尼克，他們當然渴望能再拿下一場勝利。

 

Gordon Hayward和Brown本季的狀況都不算太好，似乎還在和球隊磨合當中，不過今天首節他們兩人表現出色，賽爾提克也因此拿到了38分的高分。次節塞隊替補後衛Terry Rozier連續砍進兩顆三分球，幫助球隊領先到達9分，終場前30.1秒中鋒Al Horford上籃得手，塞爾提克以69:58進入到下半場。

 

第3節比賽進入到Irving的表演時間，他單節轟下14分，包括了3記重要的三分彈，塞爾提克也在該節結束後將分差拉開到15分。末節尼克無心再戰，塞爾提克也對比賽有了一些想法，雙方陸續開始走馬換將，比賽結果也大致底定，最終主場軍以28分之差贏球。

 

塞爾提克今天全隊命中率高達53.3%，反觀尼克只有40.9%，成為雙方勝負的分野。Irving此役攻下全場最高的22分，另外還有8次助攻，表現非常全面。而從板凳出發的Brown，則是打出讓人激賞的高效率，全場出賽24分鐘，10投7中得到21分。

 

尼克方面，Tim Hardaway Jr.也得到了22分，但19投僅7中，命中率並不理想。Emmanuel Mudiay則是拿到了17分和6次的助攻。

"""

In [2891]:
pos_title_features(test_title,15)

{'NBA': True, '主場': True, '連勝': True}

In [2892]:
get_title_featuresets(books[0],top=200)

[{'FIDO生物': True, '中華電信': True, '特徵認證': True, '生物': True, '生物特徵': True}, '證券']

In [2893]:
books[0]

[{'中華電信推FIDO生物特徵認證 刷臉快速通關': '證券'},
 {'金管會及經濟部聯手打造的Fintech Taipei台北金融科技展今天登場，其中「未來金融城」主題館結合中華電信的FIDO生物特徵認證系統，讓民眾透過人臉辨識體驗快速通關。中華電信於Fintech Taipei台北金融科技展展出3大認證服務，包含FIDO生物特徵認證解決方案、中華電信通用身分驗證服務中心（Public ID）、線上文件簽章系統（PDF Sign），為金融科技打造全方位的解決方案。中華電信表示，FIDO生物特徵認證解決方案提供安全且便利的身分認證機制，藉由指紋或人臉辨識等快速完成用戶身分認證與交易確認，代替傳統帳號密碼認證，同時強化安全、簡化交易流程。中華電信通用身分驗證服務中心透過單一標準介面，介接多元化認證服務，可提高各產業導入身分驗證機制的效率，避免重複註冊，並保有安全與隱私性，目前可支援自然人、法人、政府機關及公司行號認證。此外，中華電信推出的線上文件簽章系統能提供客戶可信賴的文件簽署服務，增進電子化流程運作機制的安全性，並可結合雲端時戳存證，運用於線上合約簽署、線上開戶、金融約定事項簽署、電子保單、電子帳單、電子畢業證書及電子公證文件等，達到文件無紙化。': '證券'}]

In [2894]:
def get_featuresets(books=books,top=200):
    title_featuresets = []
    txt_featuresets = []
    for book in books:

        title_featureset = get_title_featuresets(book,top)
        title_featuresets.append(title_featureset)
        
        txt_featureset = get_txt_featuresets(book,top)
        txt_featuresets.append(txt_featureset)
    return title_featuresets, txt_featuresets

In [2895]:
title_featuresets, txt_featuresets = get_featuresets(top=300)

生物1科技
辨識1科技
流程1科技
主題館1科技
ID1科技
指紋1科技
用戶1科技
效率1科技
證書1地方
聯手1運動
畢業1運動
臉1證券
經濟部1產經
事項1政治
生物,科技
辨識,科技
流程,科技
主題館,科技
ID,科技
指紋,科技
用戶,科技
效率,科技
庫克1科技
監管1科技
Apple1科技
用戶1科技
Facebook1科技
個資1科技
專訪1地方
場所1社會
管制1生活
自我1娛樂
頻道1娛樂
播出1娛樂
這裡1娛樂
新聞網1國際
爆發1國際
預測1產經
程度1產經
利潤1產經
法規1政治
法令1政治
錯誤1政治
片段1文化
東西1文化
庫克,科技
監管,科技
Apple,科技
用戶,科技
Facebook,科技
個資,科技
不可避免1科技
新監管1科技
用戶資料1科技
不可避免1地方
新監管1地方
用戶資料1地方
不可避免1社會
新監管1社會
用戶資料1社會
不可避免1運動
新監管1運動
用戶資料1運動
不可避免1兩岸
新監管1兩岸
用戶資料1兩岸
不可避免1證券
新監管1證券
用戶資料1證券
不可避免1生活
新監管1生活
用戶資料1生活
不可避免1娛樂
新監管1娛樂
用戶資料1娛樂
不可避免1國際
新監管1國際
用戶資料1國際
不可避免1產經
新監管1產經
用戶資料1產經
不可避免1政治
新監管1政治
用戶資料1政治
不可避免1文化
新監管1文化
用戶資料1文化
無線1科技
外媒1科技
專利1科技
Apple1科技
套1科技
用來1科技
衛星1科技
速度1科技
頻段1兩岸
看好1證券
無線,科技
外媒,科技
專利,科技
Apple,科技
套,科技
用來,科技
衛星,科技
速度,科技
報導蘋果1科技
智慧音箱1科技
毫米波1科技
無線通訊1科技
通訊網路1科技
國外科技1科技
科技網站1科技
先前報導1科技
NR技術1科技
通訊技術1科技
外媒報導1科技
網站Patently1科技
PatentlyApple1科技
Apple報導1科技
項專利1科技
專利顯示1科技
顯示蘋果1科技
指出蘋果1科技
外媒先前1科技
蘋果布局1科技
相關技術1科技
iPhone產品1科技
衛星通訊1科技
報導蘋果1地方
智慧音箱1地方
毫米波1地方
無線通訊1地方
通訊網路1地方
國外科技1地方
科技網站1地方
先前報導1地方
NR技術1地方
通訊技術1地方
外媒

套1科技
婉拒1地方
站1地方
酒店1社會
東方1運動
回到1運動
張信哲1娛樂
劉嘉玲1娛樂
開唱1娛樂
演唱1娛樂
歌手1娛樂
攻蛋1娛樂
巡演1娛樂
巨蛋1娛樂
歌迷1娛樂
獻唱1娛樂
睽違1娛樂
出道1娛樂
票房1娛樂
門票1娛樂
開賣1娛樂
重現1文化
張信哲,娛樂
劉嘉玲,娛樂
開唱,娛樂
演唱,娛樂
歌手,娛樂
攻蛋,娛樂
巡演,娛樂
巨蛋,娛樂
歌迷,娛樂
獻唱,娛樂
睽違,娛樂
出道,娛樂
票房,娛樂
門票,娛樂
開賣,娛樂
一點動心1科技
小巨蛋1科技
影片包括1科技
一直以來1科技
針對台灣1科技
台北小1科技
一點動心1地方
小巨蛋1地方
影片包括1地方
一直以來1地方
針對台灣1地方
台北小1地方
一點動心1社會
小巨蛋1社會
影片包括1社會
一直以來1社會
針對台灣1社會
台北小1社會
一點動心1運動
小巨蛋1運動
影片包括1運動
一直以來1運動
針對台灣1運動
台北小1運動
一點動心1兩岸
小巨蛋1兩岸
影片包括1兩岸
一直以來1兩岸
針對台灣1兩岸
台北小1兩岸
一點動心1證券
小巨蛋1證券
影片包括1證券
一直以來1證券
針對台灣1證券
台北小1證券
一點動心1生活
小巨蛋1生活
影片包括1生活
一直以來1生活
針對台灣1生活
台北小1生活
一點動心1娛樂
小巨蛋1娛樂
影片包括1娛樂
一直以來1娛樂
針對台灣1娛樂
台北小1娛樂
一點動心1國際
小巨蛋1國際
影片包括1國際
一直以來1國際
針對台灣1國際
台北小1國際
一點動心1產經
小巨蛋1產經
影片包括1產經
一直以來1產經
針對台灣1產經
台北小1產經
一點動心1政治
小巨蛋1政治
影片包括1政治
一直以來1政治
針對台灣1政治
台北小1政治
一點動心1文化
小巨蛋1文化
影片包括1文化
一直以來1文化
針對台灣1文化
台北小1文化
持1社會
開車1社會
勝1運動
台日1運動
入境1兩岸
短期1證券
駕照1生活
省1生活
還要1生活
台幣1娛樂
外交1國際
日方1政治
國人1政治
譯本1文化
駕照,生活
省,生活
還要,生活
駕照日文1科技
日文譯本1科技
駕照日文1地方
日文譯本1地方
駕照日文1社會
日文譯本1社會
駕照日文1運動
日文譯本1運動
駕照日文1兩岸
日文譯本1兩岸
駕照日文1證券
日文譯本1證券
駕照日文1生活
日文譯本1生活
駕照日文1娛樂
日文譯本1娛

展區1科技
主題館1科技
朱立倫1地方
迎接1地方
今1社會
回到1運動
板橋1生活
注意1生活
職人1娛樂
李安1娛樂
府中1娛樂
放映1娛樂
金馬獎1娛樂
執委會1娛樂
銀幕1娛樂
拍1娛樂
編劇1娛樂
影展1娛樂
播映1娛樂
結晶1文化
展場1文化
職人,娛樂
李安,娛樂
府中,娛樂
放映,娛樂
金馬獎,娛樂
執委會,娛樂
銀幕,娛樂
拍,娛樂
編劇,娛樂
影展,娛樂
播映,娛樂
電影職人1科技
台灣電影1科技
紀錄片放映1科技
放映院1科技
電影導演1科技
繼續努力1科技
週年推出1科技
之外台灣1科技
屆金馬1科技
執委會主席1科技
主席李安1科技
感謝李安1科技
提到當年1科技
電影職人1地方
台灣電影1地方
紀錄片放映1地方
放映院1地方
電影導演1地方
繼續努力1地方
週年推出1地方
之外台灣1地方
屆金馬1地方
執委會主席1地方
主席李安1地方
感謝李安1地方
提到當年1地方
電影職人1社會
台灣電影1社會
紀錄片放映1社會
放映院1社會
電影導演1社會
繼續努力1社會
週年推出1社會
之外台灣1社會
屆金馬1社會
執委會主席1社會
主席李安1社會
感謝李安1社會
提到當年1社會
電影職人1運動
台灣電影1運動
紀錄片放映1運動
放映院1運動
電影導演1運動
繼續努力1運動
週年推出1運動
之外台灣1運動
屆金馬1運動
執委會主席1運動
主席李安1運動
感謝李安1運動
提到當年1運動
電影職人1兩岸
台灣電影1兩岸
紀錄片放映1兩岸
放映院1兩岸
電影導演1兩岸
繼續努力1兩岸
週年推出1兩岸
之外台灣1兩岸
屆金馬1兩岸
執委會主席1兩岸
主席李安1兩岸
感謝李安1兩岸
提到當年1兩岸
電影職人1證券
台灣電影1證券
紀錄片放映1證券
放映院1證券
電影導演1證券
繼續努力1證券
週年推出1證券
之外台灣1證券
屆金馬1證券
執委會主席1證券
主席李安1證券
感謝李安1證券
提到當年1證券
電影職人1生活
台灣電影1生活
紀錄片放映1生活
放映院1生活
電影導演1生活
繼續努力1生活
週年推出1生活
之外台灣1生活
屆金馬1生活
執委會主席1生活
主席李安1生活
感謝李安1生活
提到當年1生活
電影職人1娛樂
台灣電影1娛樂
紀錄片放映1娛樂
放映院1娛樂
電影導演1娛樂
繼續努力1娛樂
週年推出1娛樂
之外台灣1娛樂
屆金馬1娛樂
執委會主席1

站1地方
女孩1社會
鈕承澤1社會
跑馬1社會
疑涉1社會
逃避1社會
警局1社會
解散1運動
劇組1娛樂
拍1娛樂
緊急1國際
爆發1國際
此事1國際
角度1文化
女孩,社會
鈕承澤,社會
跑馬,社會
疑涉,社會
逃避,社會
警局,社會
劉蔚然1科技
電影跑馬1科技
疑涉性侵1科技
女性工作1科技
臉書首度1科技
首度發聲1科技
同感悲痛1科技
期間疑涉1科技
性侵女性1科技
鈕承澤近期1科技
近期正在1科技
正在籌拍1科技
籌拍新1科技
引發外界1科技
赴警局1科技
警局說明1科技
鈕承澤疑涉1科技
司法調查1科技
劉蔚然1地方
電影跑馬1地方
疑涉性侵1地方
女性工作1地方
臉書首度1地方
首度發聲1地方
同感悲痛1地方
期間疑涉1地方
性侵女性1地方
鈕承澤近期1地方
近期正在1地方
正在籌拍1地方
籌拍新1地方
引發外界1地方
赴警局1地方
警局說明1地方
鈕承澤疑涉1地方
司法調查1地方
劉蔚然1社會
電影跑馬1社會
疑涉性侵1社會
女性工作1社會
臉書首度1社會
首度發聲1社會
同感悲痛1社會
期間疑涉1社會
性侵女性1社會
鈕承澤近期1社會
近期正在1社會
正在籌拍1社會
籌拍新1社會
引發外界1社會
赴警局1社會
警局說明1社會
鈕承澤疑涉1社會
司法調查1社會
劉蔚然1運動
電影跑馬1運動
疑涉性侵1運動
女性工作1運動
臉書首度1運動
首度發聲1運動
同感悲痛1運動
期間疑涉1運動
性侵女性1運動
鈕承澤近期1運動
近期正在1運動
正在籌拍1運動
籌拍新1運動
引發外界1運動
赴警局1運動
警局說明1運動
鈕承澤疑涉1運動
司法調查1運動
劉蔚然1兩岸
電影跑馬1兩岸
疑涉性侵1兩岸
女性工作1兩岸
臉書首度1兩岸
首度發聲1兩岸
同感悲痛1兩岸
期間疑涉1兩岸
性侵女性1兩岸
鈕承澤近期1兩岸
近期正在1兩岸
正在籌拍1兩岸
籌拍新1兩岸
引發外界1兩岸
赴警局1兩岸
警局說明1兩岸
鈕承澤疑涉1兩岸
司法調查1兩岸
劉蔚然1證券
電影跑馬1證券
疑涉性侵1證券
女性工作1證券
臉書首度1證券
首度發聲1證券
同感悲痛1證券
期間疑涉1證券
性侵女性1證券
鈕承澤近期1證券
近期正在1證券
正在籌拍1證券
籌拍新1證券
引發外界1證券
赴警局1證券
警局說明1證券
鈕承澤疑涉1證券
司法調查1證券
劉蔚然1生活
電影跑馬1生活
疑涉性侵1生活

羈押禁見1運動
彰化地方1運動
許姓樁腳1運動
聲請羈押1運動
香油錢名義1運動
萬元交保1運動
票元1運動
地檢署指出1運動
法院聲請1運動
當選人涉嫌1運動
元買票1運動
羈押禁見1兩岸
彰化地方1兩岸
許姓樁腳1兩岸
聲請羈押1兩岸
香油錢名義1兩岸
萬元交保1兩岸
票元1兩岸
地檢署指出1兩岸
法院聲請1兩岸
當選人涉嫌1兩岸
元買票1兩岸
羈押禁見1證券
彰化地方1證券
許姓樁腳1證券
聲請羈押1證券
香油錢名義1證券
萬元交保1證券
票元1證券
地檢署指出1證券
法院聲請1證券
當選人涉嫌1證券
元買票1證券
羈押禁見1生活
彰化地方1生活
許姓樁腳1生活
聲請羈押1生活
香油錢名義1生活
萬元交保1生活
票元1生活
地檢署指出1生活
法院聲請1生活
當選人涉嫌1生活
元買票1生活
羈押禁見1娛樂
彰化地方1娛樂
許姓樁腳1娛樂
聲請羈押1娛樂
香油錢名義1娛樂
萬元交保1娛樂
票元1娛樂
地檢署指出1娛樂
法院聲請1娛樂
當選人涉嫌1娛樂
元買票1娛樂
羈押禁見1國際
彰化地方1國際
許姓樁腳1國際
聲請羈押1國際
香油錢名義1國際
萬元交保1國際
票元1國際
地檢署指出1國際
法院聲請1國際
當選人涉嫌1國際
元買票1國際
羈押禁見1產經
彰化地方1產經
許姓樁腳1產經
聲請羈押1產經
香油錢名義1產經
萬元交保1產經
票元1產經
地檢署指出1產經
法院聲請1產經
當選人涉嫌1產經
元買票1產經
羈押禁見1政治
彰化地方1政治
許姓樁腳1政治
聲請羈押1政治
香油錢名義1政治
萬元交保1政治
票元1政治
地檢署指出1政治
法院聲請1政治
當選人涉嫌1政治
元買票1政治
羈押禁見1文化
彰化地方1文化
許姓樁腳1文化
聲請羈押1文化
香油錢名義1文化
萬元交保1文化
票元1文化
地檢署指出1文化
法院聲請1文化
當選人涉嫌1文化
元買票1文化
侯友宜1地方
祈福1地方
媽祖1地方
菩薩1地方
出國1地方
參拜1地方
市民1地方
僅有1地方
適當1地方
警政署1社會
背景1兩岸
幹部1兩岸
常務1兩岸
板橋1生活
負擔1生活
西門1生活
府中1娛樂
發言1娛樂
適用1產經
薪資1產經
硬體1產經
黨務1政治
點名1政治
意願1政治
一職1政治
勇氣1文化
侯友宜,地方
祈福,地方
媽祖,地方
菩薩,地方
出國,地方
參拜,地方
市民,地方
僅有,地方
適

...

甲級動員1社會
書記長曾1社會
正義條例1社會
條例規定1社會
規定促轉1社會
行政院長提名1社會
預算能夠1社會
要求促轉1社會
促轉會應1社會
全面改組1社會
代理促轉1社會
年度施政1社會
施政計畫1社會
書面報告1社會
報告促轉1社會
編列億1社會
張天欽1運動
天欽說錯1運動
說錯話1運動
轉型正義1運動
代表促轉1運動
主委副主委1運動
立法院同意1運動
審查促轉1運動
促進轉型1運動
預算編列1運動
天欽事件1運動
全面杯葛1運動
預算審查1運動
幹事長李俊俋1運動
前促轉會1運動
副主委張1運動
天欽失言1運動
失言事件1運動
立法院司法1運動
發出甲級1運動
甲級動員1運動
書記長曾1運動
正義條例1運動
條例規定1運動
規定促轉1運動
行政院長提名1運動
預算能夠1運動
要求促轉1運動
促轉會應1運動
全面改組1運動
代理促轉1運動
年度施政1運動
施政計畫1運動
書面報告1運動
報告促轉1運動
編列億1運動
張天欽1兩岸
天欽說錯1兩岸
說錯話1兩岸
轉型正義1兩岸
代表促轉1兩岸
主委副主委1兩岸
立法院同意1兩岸
審查促轉1兩岸
促進轉型1兩岸
預算編列1兩岸
天欽事件1兩岸
全面杯葛1兩岸
預算審查1兩岸
幹事長李俊俋1兩岸
前促轉會1兩岸
副主委張1兩岸
天欽失言1兩岸
失言事件1兩岸
立法院司法1兩岸
發出甲級1兩岸
甲級動員1兩岸
書記長曾1兩岸
正義條例1兩岸
條例規定1兩岸
規定促轉1兩岸
行政院長提名1兩岸
預算能夠1兩岸
要求促轉1兩岸
促轉會應1兩岸
全面改組1兩岸
代理促轉1兩岸
年度施政1兩岸
施政計畫1兩岸
書面報告1兩岸
報告促轉1兩岸
編列億1兩岸
張天欽1證券
天欽說錯1證券
說錯話1證券
轉型正義1證券
代表促轉1證券
主委副主委1證券
立法院同意1證券
審查促轉1證券
促進轉型1證券
預算編列1證券
天欽事件1證券
全面杯葛1證券
預算審查1證券
幹事長李俊俋1證券
前促轉會1證券
副主委張1證券
天欽失言1證券
失言事件1證券
立法院司法1證券
發出甲級1證券
甲級動員1證券
書記長曾1證券
正義條例1證券
條例規定1證券
規定促轉1證券
行政院長提名1證券
預算能夠1證券
要求促轉1證券
促轉會應1證券
全面改組1證券
代理促轉1證券
年度施政1證券
施政計畫1證券
書面報告1證券
報告促轉1證券
編列

戈德哈默1地方
歐洲議會1地方
法國政府1地方
背心示威1地方
發表演說1地方
歐洲聯盟1地方
聯盟EU1地方
彭博Bloomberg1地方
議會選舉1地方
馬克宏Emmanuel1地方
EmmanuelMacron1地方
示威人士1地方
全國發表1地方
發言人葛里1地方
葛里沃1地方
沃Benjamin1地方
BenjaminGriveaux1地方
場危機1地方
背心運動1地方
運動連續1地方
週末進行1地方
進行抗爭1地方
馬克宏已1地方
低工資1地方
勒德里安Jean1地方
JeanYves1地方
YvesLe1地方
LeDrian1地方
戈德哈默1社會
歐洲議會1社會
法國政府1社會
背心示威1社會
發表演說1社會
歐洲聯盟1社會
聯盟EU1社會
彭博Bloomberg1社會
議會選舉1社會
馬克宏Emmanuel1社會
EmmanuelMacron1社會
示威人士1社會
全國發表1社會
發言人葛里1社會
葛里沃1社會
沃Benjamin1社會
BenjaminGriveaux1社會
場危機1社會
背心運動1社會
運動連續1社會
週末進行1社會
進行抗爭1社會
馬克宏已1社會
低工資1社會
勒德里安Jean1社會
JeanYves1社會
YvesLe1社會
LeDrian1社會
戈德哈默1運動
歐洲議會1運動
法國政府1運動
背心示威1運動
發表演說1運動
歐洲聯盟1運動
聯盟EU1運動
彭博Bloomberg1運動
議會選舉1運動
馬克宏Emmanuel1運動
EmmanuelMacron1運動
示威人士1運動
全國發表1運動
發言人葛里1運動
葛里沃1運動
沃Benjamin1運動
BenjaminGriveaux1運動
場危機1運動
背心運動1運動
運動連續1運動
週末進行1運動
進行抗爭1運動
馬克宏已1運動
低工資1運動
勒德里安Jean1運動
JeanYves1運動
YvesLe1運動
LeDrian1運動
戈德哈默1兩岸
歐洲議會1兩岸
法國政府1兩岸
背心示威1兩岸
發表演說1兩岸
歐洲聯盟1兩岸
聯盟EU1兩岸
彭博Bloomberg1兩岸
議會選舉1兩岸
馬克宏Emmanuel1兩岸
EmmanuelMacron1兩岸
示威人士1兩岸
全國發表1兩岸
發言人葛里1兩岸
葛里沃1兩岸
沃Benjamin1兩岸
BenjaminGriveau

指揮,社會
搜索,社會
住處,社會
被告,社會
公職,社會
檢察署,社會
到案,社會
全案,社會
偵辦,社會
檢調,社會
接獲,社會
樁腳,社會
北檢,社會
調查局,社會
警察,社會
警察局,社會
分局,社會
證人,社會
陳姓里長1科技
當選人涉嫌1科技
公職人員1科技
人員選舉1科技
名陳姓1科技
元買票1科技
元代價1科技
選民買票1科技
陳姓里長1地方
當選人涉嫌1地方
公職人員1地方
人員選舉1地方
名陳姓1地方
元買票1地方
元代價1地方
選民買票1地方
陳姓里長1社會
當選人涉嫌1社會
公職人員1社會
人員選舉1社會
名陳姓1社會
元買票1社會
元代價1社會
選民買票1社會
陳姓里長1運動
當選人涉嫌1運動
公職人員1運動
人員選舉1運動
名陳姓1運動
元買票1運動
元代價1運動
選民買票1運動
陳姓里長1兩岸
當選人涉嫌1兩岸
公職人員1兩岸
人員選舉1兩岸
名陳姓1兩岸
元買票1兩岸
元代價1兩岸
選民買票1兩岸
陳姓里長1證券
當選人涉嫌1證券
公職人員1證券
人員選舉1證券
名陳姓1證券
元買票1證券
元代價1證券
選民買票1證券
陳姓里長1生活
當選人涉嫌1生活
公職人員1生活
人員選舉1生活
名陳姓1生活
元買票1生活
元代價1生活
選民買票1生活
陳姓里長1娛樂
當選人涉嫌1娛樂
公職人員1娛樂
人員選舉1娛樂
名陳姓1娛樂
元買票1娛樂
元代價1娛樂
選民買票1娛樂
陳姓里長1國際
當選人涉嫌1國際
公職人員1國際
人員選舉1國際
名陳姓1國際
元買票1國際
元代價1國際
選民買票1國際
陳姓里長1產經
當選人涉嫌1產經
公職人員1產經
人員選舉1產經
名陳姓1產經
元買票1產經
元代價1產經
選民買票1產經
陳姓里長1政治
當選人涉嫌1政治
公職人員1政治
人員選舉1政治
名陳姓1政治
元買票1政治
元代價1政治
選民買票1政治
陳姓里長1文化
當選人涉嫌1文化
公職人員1文化
人員選舉1文化
名陳姓1文化
元買票1文化
元代價1文化
選民買票1文化
飛機1科技
逃避1社會
失信1兩岸
澎湃1兩岸
升級1兩岸
月起1證券
備忘錄1國際
每月1文化
固定1文化
失信,兩岸
澎湃,兩岸
升級,兩岸
中國官方1科技
澎湃新聞1科技
國家發展1科技
中國全國1科技
中國官方1地方
澎湃新聞1地方
國家發展1地方
中國全國1地方
中國官方1社會


鈕承澤上午1運動
警局外1運動
媒體推擠1運動
目前情緒1運動
躁鬱症狀1運動
犯罪嫌疑1運動
報導鈕承澤1運動
拍攝電影1運動
電影跑馬1運動
跑馬暫定1運動
暫定片名1運動
片名期間1運動
期間疑涉1運動
疑涉性侵1運動
人員受害1運動
赴醫院1運動
醫院驗傷1運動
驗傷證實1運動
證實曾1運動
曾飽受1運動
飽受摧殘1運動
摧殘受害1運動
婦幼隊報案1運動
製作筆錄1運動
性侵女性1兩岸
女性工作1兩岸
頭部遭1兩岸
攝影機打傷1兩岸
友人陪同1兩岸
控涉性侵1兩岸
透過律師1兩岸
請假北檢1兩岸
鈕承澤疑似1兩岸
疑似涉及1兩岸
性侵案引發1兩岸
引發外界1兩岸
外界關注1兩岸
關注神隱1兩岸
神隱天後1兩岸
上午親赴1兩岸
警察局大安1兩岸
大安分局1兩岸
分局說明1兩岸
簽發傳票1兩岸
傳票交由1兩岸
交由警方1兩岸
送達鈕承澤1兩岸
鈕承澤要求1兩岸
下午時到1兩岸
時到北檢1兩岸
北檢說明1兩岸
鈕承澤未1兩岸
未現身1兩岸
現身北檢1兩岸
到庭代1兩岸
代鈕承澤1兩岸
檢察官請假1兩岸
鈕承澤上午1兩岸
警局外1兩岸
媒體推擠1兩岸
目前情緒1兩岸
躁鬱症狀1兩岸
犯罪嫌疑1兩岸
報導鈕承澤1兩岸
拍攝電影1兩岸
電影跑馬1兩岸
跑馬暫定1兩岸
暫定片名1兩岸
片名期間1兩岸
期間疑涉1兩岸
疑涉性侵1兩岸
人員受害1兩岸
赴醫院1兩岸
醫院驗傷1兩岸
驗傷證實1兩岸
證實曾1兩岸
曾飽受1兩岸
飽受摧殘1兩岸
摧殘受害1兩岸
婦幼隊報案1兩岸
製作筆錄1兩岸
性侵女性1證券
女性工作1證券
頭部遭1證券
攝影機打傷1證券
友人陪同1證券
控涉性侵1證券
透過律師1證券
請假北檢1證券
鈕承澤疑似1證券
疑似涉及1證券
性侵案引發1證券
引發外界1證券
外界關注1證券
關注神隱1證券
神隱天後1證券
上午親赴1證券
警察局大安1證券
大安分局1證券
分局說明1證券
簽發傳票1證券
傳票交由1證券
交由警方1證券
送達鈕承澤1證券
鈕承澤要求1證券
下午時到1證券
時到北檢1證券
北檢說明1證券
鈕承澤未1證券
未現身1證券
現身北檢1證券
到庭代1證券
代鈕承澤1證券
檢察官請假1證券
鈕承澤上午1證券
警局外1證券
媒體推擠1證券
目前情緒1證券
躁鬱症狀1證券
犯罪嫌疑1證券
報導鈕承澤1證券
拍攝電影1證券
電影跑馬1證券
跑馬暫定1證券
暫

儀式暨1產經
人權日紀念1產經
名單之後1產經
政治事件1產經
波名單1產經
撤銷刑事1產經
刑事有罪1政治
有罪判決1政治
判決撤銷1政治
撤銷公告1政治
高白蘭1政治
公告儀式1政治
堅守崗位1政治
遲來正義1政治
世界人權1政治
轉型正義1政治
二波刑事1政治
紀念活動1政治
政治案件1政治
政治受難1政治
受難家屬1政治
促進轉型1政治
平復司法1政治
司法不法1政治
儀式暨1政治
人權日紀念1政治
名單之後1政治
政治事件1政治
波名單1政治
撤銷刑事1政治
刑事有罪1文化
有罪判決1文化
判決撤銷1文化
撤銷公告1文化
高白蘭1文化
公告儀式1文化
堅守崗位1文化
遲來正義1文化
世界人權1文化
轉型正義1文化
二波刑事1文化
紀念活動1文化
政治案件1文化
政治受難1文化
受難家屬1文化
促進轉型1文化
平復司法1文化
司法不法1文化
儀式暨1文化
人權日紀念1文化
名單之後1文化
政治事件1文化
波名單1文化
撤銷刑事1文化
中獎1生活
派彩1生活
雙贏1生活
彩第1生活
期1生活
開獎1生活
頭獎1生活
摃龜1生活
注1生活
獎獎號1生活
台幣1娛樂
中獎,生活
派彩,生活
雙贏,生活
彩第,生活
期,生活
開獎,生活
頭獎,生活
摃龜,生活
注,生活
獎獎號,生活
雙贏彩第1科技
彩第期1科技
期今晚1科技
今晚開獎1科技
開獎中獎1科技
中獎號碼1科技
頭獎摃龜1科技
摃龜貳1科技
貳獎有1科技
獎有注1科技
注中獎1科技
萬元派彩1科技
台彩公布1科技
公布為準1科技
雙贏彩第1地方
彩第期1地方
期今晚1地方
今晚開獎1地方
開獎中獎1地方
中獎號碼1地方
頭獎摃龜1地方
摃龜貳1地方
貳獎有1地方
獎有注1地方
注中獎1地方
萬元派彩1地方
台彩公布1地方
公布為準1地方
雙贏彩第1社會
彩第期1社會
期今晚1社會
今晚開獎1社會
開獎中獎1社會
中獎號碼1社會
頭獎摃龜1社會
摃龜貳1社會
貳獎有1社會
獎有注1社會
注中獎1社會
萬元派彩1社會
台彩公布1社會
公布為準1社會
雙贏彩第1運動
彩第期1運動
期今晚1運動
今晚開獎1運動
開獎中獎1運動
中獎號碼1運動
頭獎摃龜1運動
摃龜貳1運動
貳獎有1運動
獎有注1運動
注中獎1運動
萬元派彩1運動
台彩公布1運動
公布為準1運動
雙贏彩第1兩岸
彩第期1兩岸
期今晚1兩岸
今晚開

In [2896]:
#txt_featuresets
'研究院' in [w for li in txt_fwords.values() for w in li]
books[0]

[{'中華電信推FIDO生物特徵認證 刷臉快速通關': '證券'},
 {'金管會及經濟部聯手打造的Fintech Taipei台北金融科技展今天登場，其中「未來金融城」主題館結合中華電信的FIDO生物特徵認證系統，讓民眾透過人臉辨識體驗快速通關。中華電信於Fintech Taipei台北金融科技展展出3大認證服務，包含FIDO生物特徵認證解決方案、中華電信通用身分驗證服務中心（Public ID）、線上文件簽章系統（PDF Sign），為金融科技打造全方位的解決方案。中華電信表示，FIDO生物特徵認證解決方案提供安全且便利的身分認證機制，藉由指紋或人臉辨識等快速完成用戶身分認證與交易確認，代替傳統帳號密碼認證，同時強化安全、簡化交易流程。中華電信通用身分驗證服務中心透過單一標準介面，介接多元化認證服務，可提高各產業導入身分驗證機制的效率，避免重複註冊，並保有安全與隱私性，目前可支援自然人、法人、政府機關及公司行號認證。此外，中華電信推出的線上文件簽章系統能提供客戶可信賴的文件簽署服務，增進電子化流程運作機制的安全性，並可結合雲端時戳存證，運用於線上合約簽署、線上開戶、金融約定事項簽署、電子保單、電子帳單、電子畢業證書及電子公證文件等，達到文件無紙化。': '證券'}]

In [2897]:
title_featuresets

[[{'FIDO生物': True, '中華電信': True, '特徵認證': True, '生物': True, '生物特徵': True},
  '證券'],
 [{'不可避免': True, '個資': True}, '科技'],
 [{}, '科技'],
 [{'企業家': True, '企業家峰會': True, '兩岸企業': True, '汪洋': True, '陸': True}, '兩岸'],
 [{'涉及黨務': True, '補選議題': True}, '政治'],
 [{'外交': True, '大使': True, '逮捕令': True}, '國際'],
 [{'劉嘉玲': True, '張信哲': True, '攻蛋': True}, '娛樂'],
 [{}, '生活'],
 [{'出國': True, '出國搶': True, '搶訂單': True, '春節': True}, '地方'],
 [{}, '國際'],
 [{'威力盃': True, '季軍': True, '投打': True, '陳楷升': True, '隊史': True, '隊史最佳': True},
  '運動'],
 [{'台灣電影': True, '李安': True, '職人': True, '電影職人': True}, '娛樂'],
 [{}, '產經'],
 [{'封口費': True, '彈劾': True, '彈劾川普': True, '曝光': True, '法律文件': True}, '國際'],
 [{'內戰': True, '沙國': True, '沙國聯軍': True, '聯軍': True, '葉門': True, '葉門內戰': True},
  '國際'],
 [{'勁夫': True,
   '女友': True,
   '日籍': True,
   '日籍女友': True,
   '男星': True,
   '蔣': True,
   '蔣勁夫': True},
  '娛樂'],
 [{'AI': True, 'AI超級': True, '超級電腦': True}, '科技'],
 [{'彩第': True,
   '彩第期': True,
   '期': True,
   '期開獎': True,
   '開獎': 

In [2898]:
title_featuresets = title_featuresets.copy()
size = int(len(title_featuresets)*0.7)
train_set, test_set = title_featuresets[:size], title_featuresets[size:]
title_classifier = nltk.NaiveBayesClassifier.train(train_set)
nltk.classify.accuracy(classifier, test_set)

0.5305555555555556

In [2899]:
txt_featuresets = txt_featuresets.copy()
size = int(len(txt_featuresets)*0.7)
train_set, test_set = txt_featuresets[:size], txt_featuresets[size:]
txt_classifier = nltk.NaiveBayesClassifier.train(train_set)
nltk.classify.accuracy(classifier, test_set)

0.6805555555555556

In [2900]:
title_comanswer = classifier.classify_many([i[0] for i in title_featuresets])
txt_comanswer = classifier.classify_many([i[0] for i in txt_featuresets])

In [2901]:
title_answer = [i[1] for i in title_featuresets]
txt_answer = [i[1] for i in txt_featuresets]

In [2902]:
txt_top = [list(get_top(txt,200).values())[0] for txt in [list(book[1].keys())[0] for book in books]]
txt_top

('生物', 3) 科技
('臉', 2) 證券
('辨識', 2) 科技
('流程', 2) 科技
('經濟部', 1) 產經
('庫克', 8) 科技
('監管', 5) 科技
('專訪', 4) 地方
('法規', 2) 政治
('自我', 2) 娛樂
('無線', 8) 科技
('外媒', 2) 科技
('專利', 2) 科技
('Apple', 1) 科技
('套', 1) 科技
('企業家', 7) 兩岸
('汪洋', 3) 兩岸
('開幕', 2) 文化
('專題', 2) 娛樂
('創業', 2) 兩岸
('會面', 7) 政治
('聯繫', 2) 社會
('政務', 2) 政治
('黨務', 2) 政治
('白綠', 2) 政治
('樂', 4) 國際
('玉成', 4) 國際
('召見', 4) 國際
('外交', 3) 國際
('大使', 3) 國際
('張信哲', 11) 娛樂
('劉嘉玲', 6) 娛樂
('開唱', 4) 娛樂
('演唱', 3) 娛樂
('歌手', 2) 娛樂
('駕照', 5) 生活
('譯本', 4) 文化
('省', 4) 生活
('外交', 2) 國際
('持', 2) 社會
('婉拒', 3) 地方
('出國', 3) 地方
('漁民', 2) 產經
('春節', 1) 地方
('登陸', 1) 科技
('波普', 6) 國際
('柯夫', 6) 國際
('犯下', 4) 國際
('終身', 3) 文化
('監禁', 3) 國際
('台中市隊', 6) 運動
('安打', 5) 運動
('球員', 5) 運動
('先發', 4) 運動
('敲出', 3) 運動
('職人', 8) 娛樂
('李安', 6) 娛樂
('府中', 4) 娛樂
('朱立倫', 4) 地方
('放映', 2) 娛樂
('月稅', 12) 產經
('金控', 10) 產經
('人壽', 7) 產經
('自結', 4) 證券
('虧損', 3) 證券
('柯恩', 6) 國際
('封口費', 3) 國際
('法庭', 2) 國際
('曝光', 2) 國際
('彈劾', 2) 國際
('葉門', 7) 國際
('聯軍', 5) 國際
('內戰', 4) 國際
('沙國', 4) 國際
('阿拉伯', 3) 國際
('蔣', 11) 娛樂
('

('歐陽', 10) 社會
('大智', 10) 社會
('男童', 8) 社會
('猥褻', 6) 社會
('罪', 6) 社會
('康友', 8) 證券
('輸液', 5) 證券
('疫苗', 3) 生活
('股價', 3) 證券
('股票', 2) 證券
('苗栗', 9) 社會
('鄉鎮市', 6) 地方
('徐耀昌', 4) 地方
('證書', 3) 地方
('上陣', 2) 運動
('法會', 4) 地方
('立法會', 4) 兩岸
('林卓廷', 4) 兩岸
('兆堅', 4) 兩岸
('預約', 3) 兩岸
('App', 9) 科技
('付費', 3) 科技
('Apple', 2) 科技
('手遊', 2) 證券
('旅行', 2) 科技
('後勁', 2) 運動
('拍', 2) 娛樂
('想像', 2) 文化
('好玩', 2) 運動
('惟揚', 2) 運動
('推案', 12) 產經
('櫻花', 11) 產經
('總銷', 11) 產經
('房價', 6) 產經
('坪', 4) 產經
('萎縮', 5) 產經
('物流', 2) 證券
('GDP', 1) 產經
('衰退', 1) 證券
('證券', 1) 證券
('法庭', 16) 國際
('大法庭', 16) 社會
('見解', 11) 社會
('裁判', 10) 社會
('庭', 7) 社會
('入閣', 3) 地方
('承擔', 2) 政治
('大使', 1) 國際
('上述', 1) 兩岸
('英文', 1) 生活
('員警', 3) 社會
('珍貴木', 3) 社會
('李姓', 2) 社會
('男子', 2) 社會
('缺錢', 2) 社會
('所有權人', 7) 文化
('洪氏', 6) 文化
('祖厝', 6) 文化
('文資', 4) 文化
('輔導', 4) 社會
('太空', 9) 科技
('降落', 9) 科技
('火箭', 7) 科技
('SpaceX', 6) 科技
('發射', 6) 科技
('不法', 4) 政治
('平復', 2) 政治
('二波', 2) 政治
('泰雅族', 2) 政治
('受難', 2) 政治
('曾經', 5) 文化
('趙', 3) 文化
('生前', 2) 文化
('歌手', 2) 娛樂
('少女', 1) 娛樂
('布

('男童', 6) 社會
('校方', 4) 社會
('事發', 3) 社會
('墜樓', 2) 社會
('還原', 2) 政治
('奇幻', 6) 文化
('童話', 5) 文化
('讀者', 4) 文化
('真實', 3) 文化
('百大', 2) 娛樂
('奇摩', 6) 產經
('折起', 6) 產經
('檔期', 2) 產經
('看好', 1) 證券
('App', 1) 科技
('泰雅族', 6) 政治
('邱致', 6) 政治
('民族', 3) 兩岸
('原住民族', 3) 文化
('真相', 3) 政治
('電動機車', 9) 產經
('經濟部', 5) 產經
('等級', 3) 生活
('萬輛', 3) 產經
('日期', 1) 國際
('召見', 6) 國際
('大使', 6) 國際
('殷弘', 3) 國際
('外交', 3) 國際
('財務', 2) 產經
('報', 3) 證券
('股市', 1) 證券
('走低', 1) 證券
('脫歐', 1) 國際
('表決', 1) 國際
('球員', 9) 運動
('張耀騰', 7) 運動
('冠軍戰', 4) 運動
('威力盃', 3) 運動
('少棒', 2) 運動
('自焚', 3) 兩岸
('App', 3) 科技
('程式', 1) 科技
('消防', 1) 社會
('消防局', 1) 社會
('中獎', 2) 生活
('派彩', 2) 生活
('期', 1) 生活
('開獎', 1) 生活
('頭獎', 1) 生活
('近視', 8) 科技
('科技部', 3) 科技
('干擾', 3) 生活
('藥物', 3) 證券
('產學', 2) 科技
('李國毅', 7) 娛樂
('靈異', 6) 娛樂
('卡司', 3) 娛樂
('看完', 3) 娛樂
('開拍', 3) 娛樂
('股價', 2) 證券
('攀高', 2) 證券
('漲', 2) 證券
('抗跌', 2) 證券
('台幣', 1) 娛樂
('華興', 13) 運動
('棒球', 8) 運動
('OB', 6) 運動
('南美', 3) 運動
('賽', 3) 運動
('陳菊', 9) 政治
('拜會', 7) 政治
('預算案', 6) 政治
('王金平', 5) 政治
('拜訪', 4) 政治
('薩克斯風', 20)

('南華', 4) 運動
('安打', 4) 運動
('交手', 2) 運動
('開賽', 2) 運動
('軍人', 14) 兩岸
('退役', 12) 兩岸
('星島日報', 4) 兩岸
('嚴懲', 4) 兩岸
('旗號', 4) 兩岸
('樓', 5) 社會
('消防', 4) 社會
('消防局', 2) 社會
('獲報', 2) 社會
('派員', 2) 社會
('股市', 8) 證券
('收盤', 3) 證券
('擔憂', 2) 證券
('財務', 2) 產經
('下跌', 2) 證券
('韓流', 2) 娛樂
('國民黨籍', 1) 政治
('效應', 1) 證券
('實力', 1) 運動
('興趣', 1) 生活
('男嬰', 13) 社會
('保母', 7) 社會
('帶回', 4) 社會
('三重', 4) 社會
('頭部', 3) 社會
('住院', 11) 生活
('負擔', 6) 生活
('元旦', 2) 生活
('病房', 2) 政治
('疾病', 2) 生活
('中獎', 2) 生活
('期', 1) 生活
('開獎', 1) 生活
('獎獎號', 1) 生活
('行車', 7) 生活
('巨大', 5) 產經
('美利達', 4) 證券
('台幣', 1) 娛樂
('子公司', 1) 證券
('太空', 11) 科技
('太空人', 4) 科技
('諾', 4) 科技
('聯合號', 3) 科技
('火箭', 3) 科技
('大愛', 4) 生活
('教師', 4) 生活
('得主', 2) 文化
('翻轉', 2) 生活
('愛心', 2) 地方
('建築', 3) 文化
('筆', 3) 國際
('保留', 2) 文化
('大樓', 2) 政治
('南投', 2) 地方
('柳川', 8) 地方
('耶誕', 7) 地方
('耶誕樹', 4) 地方
('豐原', 3) 地方
('點燈', 2) 地方
('退休', 7) 文化
('林懷民', 7) 文化
('雲門', 4) 文化
('舞團', 3) 文化
('舞作', 2) 文化
('上櫃', 7) 證券
('櫃買', 7) 證券
('上市', 3) 證券
('新普', 2) 證券
('環球', 2) 國際
('葉明水', 7) 產經
('拓展', 3) 產經
('秘書長', 2) 

('影視', 14) 娛樂
('影視局', 4) 娛樂
('影匯', 3) 娛樂
('市場展', 3) 娛樂
('優質', 2) 娛樂
('奧萬大', 7) 地方
('義賣', 5) 地方
('愛心', 3) 地方
('賞楓', 3) 地方
('響應', 3) 地方
('安打', 13) 運動
('敲出', 7) 運動
('韓職', 6) 運動
('佐藤', 6) 運動
('龍彥', 5) 運動
('投案', 10) 社會
('公投案', 10) 政治
('公投法', 8) 政治
('李俊俋', 7) 政治
('修法', 7) 政治
('陳金德', 13) 社會
('停業', 5) 社會
('文創', 4) 產經
('負責人', 4) 社會
('註銷', 4) 國際
('火星', 9) 科技
('機率', 3) 科技
('太空', 3) 科技
('登陸', 3) 科技
('死', 2) 社會
('居住證', 16) 兩岸
('讀取', 10) 兩岸
('RFID', 10) 兩岸
('讀卡機', 8) 兩岸
('未能', 4) 兩岸
('少年', 4) 社會
('演唱', 4) 娛樂
('桃捷', 4) 生活
('疏運', 3) 生活
('體育', 3) 運動
('Airbnb', 12) 生活
('房源', 7) 生活
('入住', 5) 生活
('房東', 5) 生活
('旅宿', 2) 生活
('圖坦卡門', 9) 文化
('博物館', 3) 文化
('少年', 2) 社會
('開幕', 2) 文化
('羅浮宮', 2) 文化
('教會', 13) 兩岸
('宗教', 10) 兩岸
('秋雨', 7) 兩岸
('帶走', 7) 兩岸
('證書', 2) 地方
('默希', 6) 國際
('穆罕默德', 3) 國際
('疾病', 2) 生活
('土耳其', 2) 國際
('女童', 1) 社會
('圓山', 12) 文化
('范欽慧', 11) 文化
('聲景', 7) 文化
('北美', 5) 證券
('成了', 3) 文化
('書展', 9) 文化
('墨西哥', 6) 文化
('李瑾', 5) 文化
('西語', 4) 文化
('漫畫', 3) 文化
('火腿', 12) 運動
('火腿隊', 10) 運動
('王柏融', 9) 運動
('桃猿', 3) 

...

('央行', 12) 產經
('硬幣', 11) 產經
('發行', 3) 娛樂
('編列', 2) 政治
('大眾', 2) 生活
('宋家豪', 7) 運動
('日圓', 4) 運動
('一軍', 4) 運動
('樂天', 3) 運動
('年薪', 2) 運動
('勇士', 7) 運動
('籃板', 3) 運動
('NBA', 2) 運動
('作客', 2) 運動
('助攻', 2) 運動
('馮', 7) 兩岸
('空服員', 6) 兩岸
('變革', 2) 兩岸
('完美', 1) 娛樂
('知', 1) 文化
('周', 4) 政治
('凱廸', 3) 兩岸
('泛民', 2) 兩岸
('建制派', 2) 兩岸
('法會', 2) 地方
('脫歐', 4) 國際
('表決', 2) 國際
('食品', 1) 政治
('農村', 1) 兩岸
('事務部', 1) 兩岸
('台籍', 6) 兩岸
('嫌犯', 6) 兩岸
('遣送', 4) 兩岸
('詐欺', 4) 社會
('陸方', 3) 兩岸
('外洩', 3) 社會
('消防', 3) 社會
('環保局', 3) 地方
('受傷', 2) 社會
('開罰', 2) 社會
('紙風車', 21) 文化
('李永豐', 12) 文化
('劇團', 6) 文化
('捐款', 4) 地方
('講', 3) 娛樂
('霸王別姬', 9) 娛樂
('張國榮', 8) 娛樂
('蝶衣', 5) 娛樂
('凱歌', 5) 娛樂
('程', 4) 娛樂
('政院', 5) 政治
('農委會', 5) 地方
('電商', 3) 證券
('爆發', 2) 國際
('人力', 2) 產經
('尤', 7) 社會
('振仲', 6) 社會
('地檢署', 3) 社會
('偵辦', 2) 社會
('台鐵', 2) 生活
('瓦希德', 16) 國際
('華人', 16) 國際
('蘇哈托', 7) 國際
('宗教', 4) 兩岸
('古斯', 2) 政治
('陸委會', 7) 兩岸
('邱垂正', 3) 兩岸
('上海市', 2) 兩岸
('陸方', 2) 兩岸
('獲准', 2) 社會
('市占', 4) 產經
('店', 2) 產經
('陸製', 2) 產經
('外媒', 1) 科技
('發言', 1) 娛樂
('金枝', 1

('相聲', 9) 文化
('馮翊綱', 9) 文化
('百場', 9) 文化
('瓦舍', 7) 文化
('生日', 3) 國際
('台幣', 5) 娛樂
('寶成', 4) 證券
('裕元', 4) 證券
('自結', 4) 證券
('子公司', 2) 證券
('紀平', 5) 運動
('梨花', 5) 運動
('奧運', 4) 運動
('大獎', 3) 生活
('得主', 2) 文化
('外交', 6) 國際
('酒會', 6) 地方
('耶誕', 6) 地方
('朱立倫', 5) 地方
('歡樂', 4) 地方
('飛機', 17) 科技
('離子', 12) 科技
('動力', 11) 科技
('風', 8) 科技
('架', 7) 科技
('Tumblr', 8) 科技
('情色', 6) 科技
('歐', 4) 科技
('部落', 3) 生活
('部落格', 3) 科技
('荔枝', 12) 地方
('刺番', 8) 地方
('釋迦', 6) 地方
('果樹', 5) 地方
('屬', 4) 社會
('節能', 3) 證券
('減碳', 3) 生活
('污染', 2) 生活
('績效', 2) 生活
('期盼', 1) 政治
('威潤', 4) 證券
('衛星', 2) 科技
('監控', 2) 科技
('車用', 1) 證券
('台幣', 1) 娛樂
('梵谷', 13) 文化
('西奧', 6) 文化
('博物館', 5) 文化
('塞爾', 3) 運動
('布魯塞爾', 3) 國際
('CPI', 7) 兩岸
('食品', 4) 政治
('增幅', 2) 產經
('低於', 1) 產經
('持平', 1) 證券
('供電', 4) 產經
('預警', 1) 兩岸
('用戶', 1) 科技
('全數', 1) 地方
('引起', 1) 生活
('受僱人員', 10) 產經
('報酬', 10) 產經
('分配', 7) 產經
('回升', 3) 生活
('GDP', 3) 產經
('桃猿', 8) 運動
('宋家豪', 6) 運動
('樂天', 5) 運動
('天母', 4) 運動
('棒球', 3) 運動
('林懷民', 10) 文化
('衛武營', 4) 文化
('劇院', 4) 文化
('滿足', 3) 產經
('退休', 3) 文化
('執

('流感', 13) 生活
('疾病', 9) 生活
('新型', 8) 生活
('疾管署', 8) 生活
('擬人', 6) 生活
('質詢', 3) 政治
('事項', 3) 政治
('法令', 2) 政治
('管制', 2) 生活
('有沒有', 2) 政治
('葫蘆墩', 6) 地方
('耶誕', 5) 地方
('自拍', 4) 地方
('耶誕樹', 3) 地方
('點燈', 3) 地方
('評比', 10) 生活
('看守', 4) 生活
('邱國書', 4) 生活
('減碳', 3) 生活
('退步', 3) 生活
('爵士', 8) 運動
('三分球', 5) 運動
('密契爾', 4) 運動
('馬刺', 4) 運動
('接連', 3) 運動
('藝術節', 7) 文化
('兩廳院', 6) 文化
('藝術家', 4) 文化
('輔助', 2) 證券
('劇場', 2) 文化
('收視', 4) 娛樂
('收視率', 4) 娛樂
('朴', 3) 娛樂
('寶劍', 3) 娛樂
('主演', 2) 娛樂
('敦泰', 5) 證券
('聯詠', 4) 證券
('暫時', 3) 證券
('聲請', 3) 社會
('駁回', 2) 社會
('黃溫恭', 8) 政治
('黃春蘭', 8) 政治
('母親', 4) 政治
('出生', 3) 文化
('槍決', 3) 政治
('紅樓', 13) 生活
('西門', 10) 生活
('自製', 3) 生活
('文創', 3) 產經
('美軍', 3) 國際
('文學', 7) 文化
('民族', 5) 兩岸
('原住民族', 5) 文化
('散文', 4) 文化
('文學獎', 2) 文化
('達欣', 9) 運動
('洋將', 4) 運動
('台啤', 4) 運動
('全場', 4) 運動
('得分', 3) 運動
('瓦斯', 9) 社會
('挖破', 5) 社會
('消防', 3) 社會
('消防局', 2) 社會
('管道', 1) 兩岸
('受傷', 2) 社會
('意外', 1) 社會
('多人', 1) 國際
('無線', 1) 科技
('時許', 1) 社會
('特赦', 4) 國際
('中東', 4) 國際
('伊朗', 3) 國際
('沙烏地', 3) 國際
('現狀', 2) 政治
('移民

('垃圾', 21) 地方
('iTrash', 11) 地方
('瓶罐', 7) 地方
('垃圾桶', 6) 地方
('皓揚', 4) 社會
('初步', 2) 社會
('四川省', 1) 兩岸
('救出', 1) 社會
('送醫', 1) 社會
('華視', 1) 娛樂
('電影節', 8) 娛樂
('記憶', 5) 文化
('專題', 4) 娛樂
('焦點', 3) 娛樂
('形式', 3) 文化
('期貨', 6) 證券
('漲', 4) 證券
('作收', 3) 證券
('成交', 3) 證券
('收', 2) 證券
('台東縣隊', 6) 運動
('陳玉船', 5) 運動
('連霸', 4) 運動
('擊敗', 4) 運動
('冠軍戰', 4) 運動
('會見', 7) 政治
('都市', 5) 地方
('黃重諺', 4) 政治
('會面', 3) 政治
('地點', 3) 科技
('科學家', 2) 科技
('地球', 2) 科技
('粒子', 2) 科技
('二氧化碳', 2) 科技
('陽光', 1) 生活
('溫哥華', 12) 國際
('引渡', 4) 國際
('伊朗', 3) 國際
('加國', 3) 國際
('受審', 2) 國際
('港', 1) 兩岸
('往返', 1) 生活
('東部', 1) 生活
('傍晚', 1) 社會
('季風', 1) 生活
('技職', 7) 生活
('教育部', 3) 生活
('瞭解', 2) 國際
('教師', 2) 生活
('機器人', 2) 科技
('戴法', 13) 國際
('瑞亞', 13) 國際
('巴西', 4) 科技
('環球', 3) 國際
('收視', 1) 娛樂
('陳淑萍', 8) 生活
('家事', 8) 生活
('家管員', 8) 生活
('管理員', 7) 生活
('轉職', 6) 生活
('反恐', 4) 兩岸
('新疆', 2) 兩岸
('處長', 1) 地方
('率團', 1) 兩岸
('電台', 1) 兩岸
('驗完', 6) 政治
('票箱', 6) 政治
('北院', 4) 政治
('聲請', 2) 社會
('計票', 2) 政治
('人力', 3) 產經
('台幣', 1) 娛樂
('報酬', 1) 產經
('報價', 1) 產經
('利潤', 1) 產經
('

['科技',
 '科技',
 '科技',
 '兩岸',
 '政治',
 '國際',
 '娛樂',
 '生活',
 '地方',
 '國際',
 '運動',
 '娛樂',
 '產經',
 '國際',
 '國際',
 '娛樂',
 '科技',
 '生活',
 '社會',
 '娛樂',
 '運動',
 '兩岸',
 '社會',
 '證券',
 '產經',
 '科技',
 '社會',
 '地方',
 '娛樂',
 '政治',
 '證券',
 '政治',
 '證券',
 '地方',
 '文化',
 '兩岸',
 '地方',
 '產經',
 '社會',
 '兩岸',
 '生活',
 '娛樂',
 '社會',
 '文化',
 '國際',
 '國際',
 '國際',
 '娛樂',
 '證券',
 '證券',
 '產經',
 '運動',
 '文化',
 '科技',
 '國際',
 '文化',
 '娛樂',
 '政治',
 '兩岸',
 '運動',
 '地方',
 '地方',
 '國際',
 '運動',
 '證券',
 '政治',
 '證券',
 '科技',
 '產經',
 '證券',
 '兩岸',
 '社會',
 '生活',
 '兩岸',
 '科技',
 '文化',
 '科技',
 '娛樂',
 '娛樂',
 '證券',
 '生活',
 '國際',
 '社會',
 '證券',
 '證券',
 '文化',
 '兩岸',
 '科技',
 '地方',
 '科技',
 '文化',
 '證券',
 '科技',
 '證券',
 '政治',
 '生活',
 '政治',
 '社會',
 '文化',
 '兩岸',
 '科技',
 '證券',
 '證券',
 '文化',
 '地方',
 '文化',
 '地方',
 '產經',
 '兩岸',
 '國際',
 '生活',
 '政治',
 '政治',
 '證券',
 '文化',
 '地方',
 '地方',
 '生活',
 '社會',
 '證券',
 '地方',
 '國際',
 '社會',
 '政治',
 '文化',
 '社會',
 '證券',
 '地方',
 '兩岸',
 '科技',
 '運動',
 '產經',
 '證券',
 '社會',
 '地方',
 '社會',
 '文化',
 '科技',
 '政治',
 '文化',
 '娛樂',
 '證券',
 '娛樂',

In [2903]:
import pandas as pd
import numpy as np

In [2904]:
title_correct = ['F' if w != title_answer[title_comanswer.index(w)] else 'T' for w in title_comanswer ]
txt_correct = ['F' if w != txt_answer[txt_comanswer.index(w)] else 'T' for w in txt_comanswer ]

In [2905]:
df = pd.DataFrame([txt_comanswer,txt_answer,txt_top,txt_correct,title_comanswer,title_answer,title_correct],index=['txt_comanswer','txt_answer','txt_top','txt_correct','title_comanswer','title_answer','title_correct']).T

In [2906]:
df.loc[df['title_correct']=='T',:]
df.head(10)

txt_comanswer txt_answer txt_top txt_correct title_comanswer title_answer  \
0            科技         證券      科技           F              證券           證券   
1            科技         科技      科技           F              科技           科技   
2            科技         科技      科技           F              國際           科技   
3            兩岸         兩岸      兩岸           T              兩岸           兩岸   
4            國際         政治      政治           F              國際           政治   
5            國際         國際      國際           F              國際           國際   
6            娛樂         娛樂      娛樂           T              娛樂           娛樂   
7            政治         生活      生活           F              國際           生活   
8            地方         地方      地方           T              國際           地方   
9            國際         國際      國際           F              國際           國際   

  title_correct  
0             T  
1             T  
2             F  
3             T  
4             F  
5             F  
6             T  
7             F  
8             F  
9             F

In [2907]:
txt_featuresets

[[{'ID': True,
   '主題館': True,
   '指紋': True,
   '效率': True,
   '流程': True,
   '生物': True,
   '用戶': True,
   '辨識': True},
  '證券'],
 [{'Apple': True,
   'Facebook': True,
   '不可避免': True,
   '個資': True,
   '庫克': True,
   '新監管': True,
   '用戶': True,
   '用戶資料': True,
   '監管': True},
  '科技'],
 [{'Apple': True,
   'Apple報導': True,
   'NR技術': True,
   'PatentlyApple': True,
   'iPhone產品': True,
   '先前報導': True,
   '國外科技': True,
   '報導蘋果': True,
   '外媒': True,
   '外媒先前': True,
   '外媒報導': True,
   '套': True,
   '專利': True,
   '專利顯示': True,
   '指出蘋果': True,
   '智慧音箱': True,
   '毫米波': True,
   '無線': True,
   '無線通訊': True,
   '用來': True,
   '相關技術': True,
   '科技網站': True,
   '網站Patently': True,
   '蘋果布局': True,
   '衛星': True,
   '衛星通訊': True,
   '通訊技術': True,
   '通訊網路': True,
   '速度': True,
   '項專利': True,
   '顯示蘋果': True},
  '科技'],
 [{'中小企業合作': True,
   '主席汪洋': True,
   '企業家': True,
   '企業家峰會': True,
   '全國政協': True,
   '兩岸企業': True,
   '創意產業': True,
   '創業': True,
   '台企': True,
   '合作交流': True,

In [2908]:
dataset = []
#answer_dict={}
answer = ""
for i,v in df.iterrows():
#    print(v)
    answer_dict={}
    print(v)
    answer_dict['txt_comanswer']=v[0]
    answer_dict['txt_top']=v[2]
    answer_dict['title_comanswer']=v[4]

    answer = v[1]
    dataset.append((answer_dict,answer))

txt_comanswer      科技
txt_answer         證券
txt_top            科技
txt_correct         F
title_comanswer    證券
title_answer       證券
title_correct       T
Name: 0, dtype: object
txt_comanswer      科技
txt_answer         科技
txt_top            科技
txt_correct         F
title_comanswer    科技
title_answer       科技
title_correct       T
Name: 1, dtype: object
txt_comanswer      科技
txt_answer         科技
txt_top            科技
txt_correct         F
title_comanswer    國際
title_answer       科技
title_correct       F
Name: 2, dtype: object
txt_comanswer      兩岸
txt_answer         兩岸
txt_top            兩岸
txt_correct         T
title_comanswer    兩岸
title_answer       兩岸
title_correct       T
Name: 3, dtype: object
txt_comanswer      國際
txt_answer         政治
txt_top            政治
txt_correct         F
title_comanswer    國際
title_answer       政治
title_correct       F
Name: 4, dtype: object
txt_comanswer      國際
txt_answer         國際
txt_top            國際
txt_correct         F
title_comanswer    國際
title

Name: 75, dtype: object
txt_comanswer      科技
txt_answer         科技
txt_top            科技
txt_correct         F
title_comanswer    科技
title_answer       科技
title_correct       T
Name: 76, dtype: object
txt_comanswer      娛樂
txt_answer         娛樂
txt_top            娛樂
txt_correct         T
title_comanswer    國際
title_answer       娛樂
title_correct       F
Name: 77, dtype: object
txt_comanswer      娛樂
txt_answer         娛樂
txt_top            娛樂
txt_correct         T
title_comanswer    娛樂
title_answer       娛樂
title_correct       T
Name: 78, dtype: object
txt_comanswer      國際
txt_answer         產經
txt_top            證券
txt_correct         F
title_comanswer    產經
title_answer       產經
title_correct       T
Name: 79, dtype: object
txt_comanswer      生活
txt_answer         生活
txt_top            生活
txt_correct         T
title_comanswer    生活
title_answer       生活
title_correct       T
Name: 80, dtype: object
txt_comanswer      國際
txt_answer         國際
txt_top            國際
txt_correct         

Name: 165, dtype: object
txt_comanswer      國際
txt_answer         證券
txt_top            證券
txt_correct         F
title_comanswer    證券
title_answer       證券
title_correct       T
Name: 166, dtype: object
txt_comanswer      社會
txt_answer         地方
txt_top            地方
txt_correct         T
title_comanswer    國際
title_answer       地方
title_correct       F
Name: 167, dtype: object
txt_comanswer      社會
txt_answer         社會
txt_top            社會
txt_correct         T
title_comanswer    社會
title_answer       社會
title_correct       T
Name: 168, dtype: object
txt_comanswer      科技
txt_answer         科技
txt_top            科技
txt_correct         F
title_comanswer    國際
title_answer       科技
title_correct       F
Name: 169, dtype: object
txt_comanswer      國際
txt_answer         國際
txt_top            國際
txt_correct         F
title_comanswer    國際
title_answer       國際
title_correct       F
Name: 170, dtype: object
txt_comanswer      科技
txt_answer         科技
txt_top            科技
txt_correct   

Name: 254, dtype: object
txt_comanswer      國際
txt_answer         國際
txt_top            國際
txt_correct         F
title_comanswer    國際
title_answer       國際
title_correct       F
Name: 255, dtype: object
txt_comanswer      社會
txt_answer         證券
txt_top            證券
txt_correct         T
title_comanswer    國際
title_answer       證券
title_correct       F
Name: 256, dtype: object
txt_comanswer      運動
txt_answer         運動
txt_top            運動
txt_correct         T
title_comanswer    運動
title_answer       運動
title_correct       T
Name: 257, dtype: object
txt_comanswer      娛樂
txt_answer         國際
txt_top            科技
txt_correct         T
title_comanswer    國際
title_answer       國際
title_correct       F
Name: 258, dtype: object
txt_comanswer      生活
txt_answer         生活
txt_top            生活
txt_correct         T
title_comanswer    生活
title_answer       生活
title_correct       T
Name: 259, dtype: object
txt_comanswer      科技
txt_answer         科技
txt_top            科技
txt_correct   

txt_comanswer      社會
txt_answer         社會
txt_top            社會
txt_correct         T
title_comanswer    社會
title_answer       社會
title_correct       T
Name: 360, dtype: object
txt_comanswer      社會
txt_answer         社會
txt_top            社會
txt_correct         T
title_comanswer    生活
title_answer       社會
title_correct       T
Name: 361, dtype: object
txt_comanswer      證券
txt_answer         生活
txt_top            生活
txt_correct         F
title_comanswer    國際
title_answer       生活
title_correct       F
Name: 362, dtype: object
txt_comanswer      文化
txt_answer         文化
txt_top            文化
txt_correct         T
title_comanswer    國際
title_answer       文化
title_correct       F
Name: 363, dtype: object
txt_comanswer      國際
txt_answer         生活
txt_top            運動
txt_correct         F
title_comanswer    國際
title_answer       生活
title_correct       F
Name: 364, dtype: object
txt_comanswer      產經
txt_answer         產經
txt_top            產經
txt_correct         T
title_comanswer  

...

Name: 774, dtype: object
txt_comanswer      產經
txt_answer         生活
txt_top            生活
txt_correct         T
title_comanswer    國際
title_answer       生活
title_correct       F
Name: 775, dtype: object
txt_comanswer      運動
txt_answer         運動
txt_top            運動
txt_correct         T
title_comanswer    運動
title_answer       運動
title_correct       T
Name: 776, dtype: object
txt_comanswer      科技
txt_answer         地方
txt_top            地方
txt_correct         F
title_comanswer    科技
title_answer       地方
title_correct       T
Name: 777, dtype: object
txt_comanswer      國際
txt_answer         兩岸
txt_top            兩岸
txt_correct         F
title_comanswer    國際
title_answer       兩岸
title_correct       F
Name: 778, dtype: object
txt_comanswer      科技
txt_answer         科技
txt_top            科技
txt_correct         F
title_comanswer    科技
title_answer       科技
title_correct       T
Name: 779, dtype: object
txt_comanswer      產經
txt_answer         產經
txt_top            產經
txt_correct   

Name: 863, dtype: object
txt_comanswer      國際
txt_answer         政治
txt_top            政治
txt_correct         F
title_comanswer    國際
title_answer       政治
title_correct       F
Name: 864, dtype: object
txt_comanswer      娛樂
txt_answer         娛樂
txt_top            娛樂
txt_correct         T
title_comanswer    娛樂
title_answer       娛樂
title_correct       T
Name: 865, dtype: object
txt_comanswer      兩岸
txt_answer         兩岸
txt_top            兩岸
txt_correct         T
title_comanswer    國際
title_answer       兩岸
title_correct       F
Name: 866, dtype: object
txt_comanswer      生活
txt_answer         生活
txt_top            生活
txt_correct         T
title_comanswer    生活
title_answer       生活
title_correct       T
Name: 867, dtype: object
txt_comanswer      社會
txt_answer         社會
txt_top            社會
txt_correct         T
title_comanswer    社會
title_answer       社會
title_correct       T
Name: 868, dtype: object
txt_comanswer      產經
txt_answer         地方
txt_top            地方
txt_correct   

Name: 968, dtype: object
txt_comanswer      文化
txt_answer         文化
txt_top            文化
txt_correct         T
title_comanswer    文化
title_answer       文化
title_correct       F
Name: 969, dtype: object
txt_comanswer      證券
txt_answer         證券
txt_top            證券
txt_correct         F
title_comanswer    國際
title_answer       證券
title_correct       F
Name: 970, dtype: object
txt_comanswer      產經
txt_answer         產經
txt_top            產經
txt_correct         T
title_comanswer    國際
title_answer       產經
title_correct       F
Name: 971, dtype: object
txt_comanswer      國際
txt_answer         地方
txt_top            地方
txt_correct         F
title_comanswer    地方
title_answer       地方
title_correct       T
Name: 972, dtype: object
txt_comanswer      兩岸
txt_answer         兩岸
txt_top            兩岸
txt_correct         T
title_comanswer    兩岸
title_answer       兩岸
title_correct       T
Name: 973, dtype: object
txt_comanswer      運動
txt_answer         運動
txt_top            運動
txt_correct   

Name: 1072, dtype: object
txt_comanswer      運動
txt_answer         運動
txt_top            運動
txt_correct         T
title_comanswer    國際
title_answer       運動
title_correct       F
Name: 1073, dtype: object
txt_comanswer      國際
txt_answer         證券
txt_top            證券
txt_correct         F
title_comanswer    證券
title_answer       證券
title_correct       T
Name: 1074, dtype: object
txt_comanswer      證券
txt_answer         證券
txt_top            證券
txt_correct         F
title_comanswer    國際
title_answer       證券
title_correct       F
Name: 1075, dtype: object
txt_comanswer      證券
txt_answer         證券
txt_top            證券
txt_correct         F
title_comanswer    國際
title_answer       證券
title_correct       F
Name: 1076, dtype: object
txt_comanswer      娛樂
txt_answer         娛樂
txt_top            娛樂
txt_correct         T
title_comanswer    娛樂
title_answer       娛樂
title_correct       T
Name: 1077, dtype: object
txt_comanswer      政治
txt_answer         政治
txt_top            政治
txt_corr

Name: 1192, dtype: object
txt_comanswer      社會
txt_answer         社會
txt_top            社會
txt_correct         T
title_comanswer    社會
title_answer       社會
title_correct       T
Name: 1193, dtype: object
txt_comanswer      文化
txt_answer         文化
txt_top            文化
txt_correct         T
title_comanswer    文化
title_answer       文化
title_correct       F
Name: 1194, dtype: object
txt_comanswer      國際
txt_answer         產經
txt_top            產經
txt_correct         F
title_comanswer    國際
title_answer       產經
title_correct       F
Name: 1195, dtype: object
txt_comanswer      運動
txt_answer         運動
txt_top            運動
txt_correct         T
title_comanswer    國際
title_answer       運動
title_correct       F
Name: 1196, dtype: object
txt_comanswer      政治
txt_answer         產經
txt_top            政治
txt_correct         F
title_comanswer    產經
title_answer       產經
title_correct       T
Name: 1197, dtype: object
txt_comanswer      政治
txt_answer         政治
txt_top            政治
txt_corr

In [2909]:
dataset[:]

[({'title_comanswer': '證券', 'txt_comanswer': '科技', 'txt_top': '科技'}, '證券'),
 ({'title_comanswer': '科技', 'txt_comanswer': '科技', 'txt_top': '科技'}, '科技'),
 ({'title_comanswer': '國際', 'txt_comanswer': '科技', 'txt_top': '科技'}, '科技'),
 ({'title_comanswer': '兩岸', 'txt_comanswer': '兩岸', 'txt_top': '兩岸'}, '兩岸'),
 ({'title_comanswer': '國際', 'txt_comanswer': '國際', 'txt_top': '政治'}, '政治'),
 ({'title_comanswer': '國際', 'txt_comanswer': '國際', 'txt_top': '國際'}, '國際'),
 ({'title_comanswer': '娛樂', 'txt_comanswer': '娛樂', 'txt_top': '娛樂'}, '娛樂'),
 ({'title_comanswer': '國際', 'txt_comanswer': '政治', 'txt_top': '生活'}, '生活'),
 ({'title_comanswer': '國際', 'txt_comanswer': '地方', 'txt_top': '地方'}, '地方'),
 ({'title_comanswer': '國際', 'txt_comanswer': '國際', 'txt_top': '國際'}, '國際'),
 ({'title_comanswer': '運動', 'txt_comanswer': '運動', 'txt_top': '運動'}, '運動'),
 ({'title_comanswer': '娛樂', 'txt_comanswer': '娛樂', 'txt_top': '娛樂'}, '娛樂'),
 ({'title_comanswer': '國際', 'txt_comanswer': '證券', 'txt_top': '產經'}, '產經'),
 ({'title_co

In [2910]:
df

txt_comanswer txt_answer txt_top txt_correct title_comanswer  \
0               科技         證券      科技           F              證券   
1               科技         科技      科技           F              科技   
2               科技         科技      科技           F              國際   
3               兩岸         兩岸      兩岸           T              兩岸   
4               國際         政治      政治           F              國際   
5               國際         國際      國際           F              國際   
6               娛樂         娛樂      娛樂           T              娛樂   
7               政治         生活      生活           F              國際   
8               地方         地方      地方           T              國際   
9               國際         國際      國際           F              國際   
10              運動         運動      運動           T              運動   
11              娛樂         娛樂      娛樂           T              娛樂   
12              證券         產經      產經           F              國際   
13              國際         國際      國際           F              國際   
14              國際         國際      國際           F              國際   
15              娛樂         娛樂      娛樂           T              娛樂   
16              政治         科技      科技           F              國際   
17              生活         生活      生活           T              生活   
18              社會         社會      社會           T              社會   
19              娛樂         娛樂      娛樂           T              娛樂   
20              運動         科技      運動           T              文化   
21              兩岸         產經      兩岸           T              國際   
22              社會         社會      社會           T              社會   
23              國際         證券      證券           F              證券   
24              國際         產經      產經           F              國際   
25              科技         科技      科技           F              科技   
26              社會         社會      社會           T              社會   
27              地方         地方      地方           T              地方   
28              國際         娛樂      娛樂           F              國際   
29              政治         政治      政治           F              國際   
...            ...        ...     ...         ...             ...   
1170            兩岸         兩岸      兩岸           T              兩岸   
1171            國際         地方      地方           F              國際   
1172            證券         證券      證券           F              國際   
1173            國際         生活      生活           F              國際   
1174            證券         證券      證券           F              證券   
1175            國際         政治      政治           F              政治   
1176            國際         兩岸      兩岸           F              兩岸   
1177            國際         文化      文化           F              娛樂   
1178            國際         政治      政治           F              國際   
1179            社會         社會      社會           T              社會   
1180            娛樂         娛樂      娛樂           T              國際   
1181            國際         產經      產經           F              國際   
1182            國際         國際      國際           F              國際   
1183            國際         國際      國際           F              國際   
1184            國際         國際      國際           F              國際   
1185            科技         科技      科技           F              科技   
1186            國際         政治      政治           F              國際   
1187            運動         運動      運動           T              運動   
1188            社會         社會      社會           T              社會   
1189            國際         兩岸      兩岸           F              國際   
1190            政治         政治      政治           F              政治   
1191            證券         證券      證券           F              證券   
1192            產經         產經      產經           T              產經   
1193            社會         社會      社會           T              社會   
1194            文化         文化      文化           T              文化   
1195            國際         產經      產經           F              國際   
119

In [2911]:
#len([i for i in get_featuresets(top = 5)[0][size:] if i[0]=={}])

In [2912]:
size = int(len(dataset)*0.7)
train_data, test_data = dataset[:size], dataset[size:]

In [2913]:
test_data2 = [i[0] for i in test_data]

In [2914]:
from nltk.classify import SklearnClassifier
from sklearn.naive_bayes import BernoulliNB
from sklearn.svm import SVC

In [2915]:
classif0 = SklearnClassifier(BernoulliNB()).train(train_data)

In [2916]:
classif0.classify_many(test_data2)
classif = SklearnClassifier(SVC(), sparse=False).train(train_data)
classif.classify_many(test_data2)

['國際',
 '國際',
 '政治',
 '地方',
 '產經',
 '生活',
 '地方',
 '娛樂',
 '生活',
 '生活',
 '產經',
 '社會',
 '運動',
 '產經',
 '兩岸',
 '政治',
 '國際',
 '運動',
 '產經',
 '兩岸',
 '政治',
 '兩岸',
 '兩岸',
 '科技',
 '政治',
 '娛樂',
 '兩岸',
 '生活',
 '社會',
 '地方',
 '運動',
 '社會',
 '產經',
 '文化',
 '證券',
 '運動',
 '地方',
 '科技',
 '科技',
 '地方',
 '生活',
 '證券',
 '文化',
 '產經',
 '產經',
 '產經',
 '運動',
 '文化',
 '兩岸',
 '運動',
 '地方',
 '科技',
 '兩岸',
 '國際',
 '社會',
 '文化',
 '證券',
 '生活',
 '科技',
 '社會',
 '兩岸',
 '政治',
 '科技',
 '社會',
 '社會',
 '兩岸',
 '地方',
 '證券',
 '產經',
 '政治',
 '文化',
 '國際',
 '證券',
 '國際',
 '兩岸',
 '兩岸',
 '運動',
 '兩岸',
 '生活',
 '社會',
 '兩岸',
 '國際',
 '兩岸',
 '國際',
 '科技',
 '生活',
 '政治',
 '兩岸',
 '國際',
 '兩岸',
 '產經',
 '政治',
 '娛樂',
 '國際',
 '國際',
 '證券',
 '地方',
 '運動',
 '娛樂',
 '運動',
 '兩岸',
 '產經',
 '國際',
 '證券',
 '文化',
 '產經',
 '產經',
 '產經',
 '生活',
 '娛樂',
 '國際',
 '兩岸',
 '文化',
 '娛樂',
 '科技',
 '生活',
 '生活',
 '證券',
 '生活',
 '國際',
 '運動',
 '娛樂',
 '國際',
 '科技',
 '運動',
 '生活',
 '科技',
 '文化',
 '運動',
 '文化',
 '證券',
 '產經',
 '地方',
 '兩岸',
 '運動',
 '娛樂',
 '產經',
 '社會',
 '兩岸',
 '地方',
 '地方',
 '兩岸',
 '娛樂',

In [2917]:
ch = []
n=0
for f in dataset[size:] :
    ch.append([f,classif.classify_many(test_data2)[n]])
    n += 1


ch

[[({'title_comanswer': '娛樂', 'txt_comanswer': '娛樂', 'txt_top': '國際'}, '娛樂'),
  '國際'],
 [({'title_comanswer': '國際', 'txt_comanswer': '國際', 'txt_top': '國際'}, '國際'),
  '國際'],
 [({'title_comanswer': '國際', 'txt_comanswer': '政治', 'txt_top': '政治'}, '政治'),
  '政治'],
 [({'title_comanswer': '國際', 'txt_comanswer': '國際', 'txt_top': '地方'}, '地方'),
  '地方'],
 [({'title_comanswer': '國際', 'txt_comanswer': '產經', 'txt_top': '產經'}, '產經'),
  '產經'],
 [({'title_comanswer': '生活', 'txt_comanswer': '生活', 'txt_top': '生活'}, '生活'),
  '生活'],
 [({'title_comanswer': '國際', 'txt_comanswer': '地方', 'txt_top': '地方'}, '地方'),
  '地方'],
 [({'title_comanswer': '娛樂', 'txt_comanswer': '娛樂', 'txt_top': '娛樂'}, '娛樂'),
  '娛樂'],
 [({'title_comanswer': '國際', 'txt_comanswer': '政治', 'txt_top': '生活'}, '生活'),
  '生活'],
 [({'title_comanswer': '國際', 'txt_comanswer': '產經', 'txt_top': '生活'}, '兩岸'),
  '生活'],
 [({'title_comanswer': '國際', 'txt_comanswer': '證券', 'txt_top': '產經'}, '產經'),
  '產經'],
 [({'title_comanswer': '國際', 'txt_comanswer': '國際', 't

In [2918]:
back = classif.classify_many(test_data2)
[i[1] for i in test_data]

['娛樂',
 '國際',
 '政治',
 '地方',
 '產經',
 '生活',
 '地方',
 '娛樂',
 '生活',
 '兩岸',
 '產經',
 '產經',
 '運動',
 '產經',
 '兩岸',
 '政治',
 '國際',
 '運動',
 '產經',
 '兩岸',
 '政治',
 '兩岸',
 '兩岸',
 '科技',
 '政治',
 '娛樂',
 '兩岸',
 '生活',
 '社會',
 '地方',
 '運動',
 '社會',
 '產經',
 '文化',
 '證券',
 '運動',
 '地方',
 '科技',
 '科技',
 '地方',
 '政治',
 '證券',
 '文化',
 '兩岸',
 '產經',
 '產經',
 '運動',
 '文化',
 '兩岸',
 '運動',
 '地方',
 '國際',
 '兩岸',
 '國際',
 '產經',
 '文化',
 '證券',
 '生活',
 '科技',
 '社會',
 '兩岸',
 '政治',
 '科技',
 '社會',
 '生活',
 '兩岸',
 '地方',
 '證券',
 '產經',
 '政治',
 '文化',
 '文化',
 '產經',
 '國際',
 '產經',
 '兩岸',
 '運動',
 '兩岸',
 '生活',
 '地方',
 '兩岸',
 '國際',
 '兩岸',
 '國際',
 '科技',
 '國際',
 '政治',
 '兩岸',
 '國際',
 '產經',
 '產經',
 '政治',
 '娛樂',
 '國際',
 '兩岸',
 '證券',
 '地方',
 '運動',
 '娛樂',
 '運動',
 '兩岸',
 '產經',
 '國際',
 '產經',
 '文化',
 '產經',
 '產經',
 '產經',
 '生活',
 '娛樂',
 '國際',
 '兩岸',
 '文化',
 '娛樂',
 '科技',
 '生活',
 '政治',
 '證券',
 '生活',
 '國際',
 '運動',
 '娛樂',
 '國際',
 '科技',
 '運動',
 '生活',
 '科技',
 '文化',
 '運動',
 '文化',
 '證券',
 '產經',
 '地方',
 '兩岸',
 '運動',
 '娛樂',
 '產經',
 '社會',
 '產經',
 '地方',
 '地方',
 '兩岸',
 '娛樂',

In [2919]:
n = 0
p=0
while n < len(back):
    if back[n] ==  [i[1] for i in test_data][n]:
 #       print([back[n], [i[1] for i in test_data][n]])
        p += 1
    n += 1
print(p)
print(p/len(back))
    

327
0.9083333333333333


In [2920]:
test_news="""
資深媒體人劉寶傑確定向主持11年的《關鍵時刻》請辭，將在明年1月永久交出主持棒，他超生動的主持方式，樹立獨特個人風格，深獲不少觀眾喜愛，因此告別《關鍵》後的下一步一直備受矚目，有消息傳出，劉寶傑之後將轉戰年代，取代跟《關鍵》同時段的《新聞追追追》。

檢視相片
▲劉寶傑下一步動向備受矚目。（圖／翻攝自臉書）

年代《新聞追追追》由主播安幼琪與張啟楷搭檔主持7年，不過《自由時報》報導，劉寶傑可能到年代，《追追追》恐怕面臨收攤危機，但年代內部知情人士指出，電視台的老闆政治立場和劉寶傑不同，挖角的機率應該不大，認為節目不會收攤，但可能會轉型或改節目名稱，主持人或許也會有變動。

檢視相片
▲《新聞追追追》恐收攤？（圖／翻攝自YouTube）

對此，安幼琪透露上周公司內部確實有開會，但只是針對節目來賓的選擇做小調整，希望能夠多聽年輕人的聲音，也表示跟搭檔張啟楷合作得很愉快，而張啟楷則回應沒有聽過類似的消息。

"""
f = pos_txt_features(test_news,100)
t =  pos_title_features(test_news,300)

print(classifier.classify(f))
print(classifier.classify(t))
print(f)

一步1科技
機率1科技
自由時報1社會
轉戰1運動
主持1娛樂
主持棒1娛樂
喜愛1娛樂
聽1娛樂
危機1國際
知情1國際
主持,娛樂
主持棒,娛樂
喜愛,娛樂
聽,娛樂
觀眾喜愛1科技
觀眾喜愛1地方
觀眾喜愛1社會
觀眾喜愛1運動
觀眾喜愛1兩岸
觀眾喜愛1證券
觀眾喜愛1生活
觀眾喜愛1娛樂
觀眾喜愛1國際
觀眾喜愛1產經
觀眾喜愛1政治
觀眾喜愛1文化
娛樂
娛樂
{'主持': True, '主持棒': True, '喜愛': True, '聽': True, '觀眾喜愛': True}


In [2921]:
def get_lab(title='',txt='',top=200):
    f = pos_txt_features(txt,top)
    t =  pos_title_features(title,top)
    top = list(get_top(txt,top).values())[0]
    print(top)
#    t = get_title_featuresets([txt,top])
#    f = get_txt_featuresets([title,top])
    if len(t.keys()) < 2:
        final = classif.classify_many({'txt_comanswer': classifier.classify(f),'txt_top':top})
        final_title = ""
    elif classifier.classify(t) == classifier.classify(f) and classifier.classify(f)==top and top == classifier.classify(t):
        final = classifier.classify(f)
        final_title = classifier.classify(t)
    else:
        final = classif.classify_many({'title_comanswer': classifier.classify(t), 'txt_comanswer': classifier.classify(f),'txt_top':top})
        final_title = classifier.classify(t)
    print(f)
    print([final_title,classifier.classify(f)])
#    print(classifier.classify(t))
    return final

In [2922]:
test_title="""
籲國人別再出言刺激日本 謝長廷挨轟「助」日代表


"""

In [2923]:
test_txt="""
日本外相河野太郎 7 日指出，台灣日前公投通過反對日本核災 5 縣食品進口一事，可能影響到台灣能否加入跨太平洋夥伴全面進步協定（CPTPP）。對此，我駐日代表謝長廷表示，將持續與日方溝通，也希望少數國人不要再出言刺激日本。此話一出，讓網友群起嘲諷，怒轟他根本是「助日代表」。



河野太郎 7 日對台灣公投通過反日本核災 5 縣食品進口一事表態，認為食品管制要有科學根據，且台灣此舉可能違反 WTO 規則，日方不排除向 WTO 申訴，而台灣想加入 CPTPP ，但可能會因為此事而受到影響，他感到相當遺憾。



檢視相片
▲日本外相河野太郎表示，台灣想加入跨太平洋夥伴全面進步協定（CPTPP）「可能因為這樣的事態而變得無法參加，非常遺憾」。（圖／翻攝自河野太郎twitter）



據《中央社》報導，駐日代表謝長廷 7 日晚間在東京出席活動，受訪時對此表示，將持續與日本積極溝通、說明，畢竟台灣是民主社會，對公投結果基本上要尊重，希望不會因此影響到台灣跟日本的友好關係，並向國人喊話，希望少數民眾不要再出言刺激日本，一直說「日本不敢啦」、「日本如果怎麼樣，日本自己吃虧」這類的話，這樣的刺激性言論沒有意義。



被問到可否預想到日本會採取什麼報復措施時，謝長廷表示不敢預測，希望國內不要再刺激日方，且日本內部也有不同意見，有人認為不對此事做出反應，若其他國家也用民粹表決，可能會影響到自由貿易；也有人認為這是台灣的民主制度，可以體諒。



至於有人認為南韓不理日本，「南韓能，台灣為何不能？」謝長廷則說，南韓無求於日本，但台灣有很多事需要拜託日本幫忙，像爭取加入 CPTPP 、希望日本在 WHO 等國際組織上幫台灣發聲等，如果退到跟南韓一樣，對台灣會是一大損失。謝長廷指出，台灣對於日本食品的管制還是比中國大陸寬鬆，但中國大陸、香港都在放寬，但台灣卻在緊縮，日本人的感受很不一樣。



謝長廷這番言論在 PTT 引發熱議，鄉民們紛紛留言砲轟「助日代表」、「出言刺激日本？噁心耶，你領哪一國薪水啊」、「日本政府過去從來沒有在國際場合幫台灣講話過，從來沒有」、「臺日友好是講民間，日本政府過去怎麼欺負臺灣」、「打一開始就沒要讓我們參加不是嗎，每年貿易逆差有多少知道嗎？次級品不良品改標賣來台灣，有負責過嗎？想想大創、阻尼器，國際沒有友誼，只有利益」、「政府怪網友刺激外國？這...」。
"""

In [2924]:
get_lab(title=test_title,txt=test_txt,top=200)

想到1地方
紛紛1地方
少數1兩岸
管制1生活
留言1娛樂
講1娛樂
刺激1國際
此事1國際
根本1國際
反1國際
此舉1國際
喊話1國際
問到1國際
報復1國際
表決1國際
WTO1產經
預測1產經
食品1政治
日方1政治
國人1政治
外國1政治
刺激,國際
此事,國際
根本,國際
反,國際
此舉,國際
喊話,國際
問到,國際
報復,國際
表決,國際
此表示1科技
認為這是1科技
此表示1地方
認為這是1地方
此表示1社會
認為這是1社會
此表示1運動
認為這是1運動
此表示1兩岸
認為這是1兩岸
此表示1證券
認為這是1證券
此表示1生活
認為這是1生活
此表示1娛樂
認為這是1娛樂
此表示1國際
認為這是1國際
此表示1產經
認為這是1產經
此表示1政治
認為這是1政治
此表示1文化
認為這是1文化
('刺激', 6) 國際
('食品', 4) 政治
('日方', 3) 政治
('少數', 2) 兩岸
('國人', 2) 政治
政治
{'刺激': True, '此事': True, '根本': True, '反': True, '此舉': True, '喊話': True, '問到': True, '報復': True, '表決': True, '此表示': True, '認為這是': True}
['', '國際']


['政治']

In [2925]:
pos_title_features(test_title,300)

{'助': True}

In [2926]:
for i in list(pos_txt_features(test_txt,300).keys()):
    print([i,i in txt_fwords['娛樂']])

想到1地方
紛紛1地方
少數1兩岸
管制1生活
留言1娛樂
講1娛樂
刺激1國際
此事1國際
根本1國際
反1國際
此舉1國際
喊話1國際
問到1國際
報復1國際
表決1國際
WTO1產經
預測1產經
食品1政治
日方1政治
國人1政治
外國1政治
刺激,國際
此事,國際
根本,國際
反,國際
此舉,國際
喊話,國際
問到,國際
報復,國際
表決,國際
此表示1科技
認為這是1科技
此表示1地方
認為這是1地方
此表示1社會
認為這是1社會
此表示1運動
認為這是1運動
此表示1兩岸
認為這是1兩岸
此表示1證券
認為這是1證券
此表示1生活
認為這是1生活
此表示1娛樂
認為這是1娛樂
此表示1國際
認為這是1國際
此表示1產經
認為這是1產經
此表示1政治
認為這是1政治
此表示1文化
認為這是1文化
['刺激', False]
['此事', False]
['根本', False]
['反', False]
['此舉', False]
['喊話', False]
['問到', False]
['報復', False]
['表決', False]
['此表示', False]
['認為這是', False]


In [2927]:
txt_fwords['娛樂']

['專輯',
 '金馬獎',
 '歌手',
 '蔡依林',
 '悲傷',
 '張國榮',
 '傅榆',
 '霸王別姬',
 'MV',
 '徐楓',
 '票房',
 '影視',
 '青春',
 '鞏俐',
 '收視',
 '金球獎',
 '飾演',
 '華視',
 '安迪',
 '電影節',
 '頻道',
 '發言',
 '李安',
 '主演',
 '歌',
 '人氣',
 'Netflix',
 '李千',
 '唱片',
 '吳恬敏',
 '播出',
 '六人',
 '凱歌',
 '劇情',
 '放映',
 '影',
 '娛樂',
 '韓流',
 '凱文哈特',
 '片中',
 '女星',
 '行',
 '執導',
 '奧斯卡',
 '新歌',
 '戲院',
 '跨年',
 '伯格',
 '盧貝松',
 '愛情',
 '主持',
 '流行',
 '開唱',
 '府中',
 '通靈',
 '海綿',
 '嚴正嵐',
 '卡司',
 '拍',
 '王力宏',
 '劇中',
 'the',
 '饒舌',
 '播映',
 '同志',
 '步理',
 '惠子',
 'I',
 '張信哲',
 '少女',
 '愛上',
 '紅毯',
 '蔣',
 '勁夫',
 '寶寶',
 '重映',
 '銀幕',
 '一年',
 '殺青',
 '影展',
 '囡仔',
 '睽違',
 '演唱',
 '樂團',
 '發行',
 '配角',
 '市場展',
 '講',
 '好萊塢',
 '瘋狂',
 '金曲',
 '林志玲',
 '壓軸',
 '宋芸樺',
 '留言',
 'Jolin',
 '修復版',
 '開拍',
 '片',
 '查某',
 '葛萊美獎',
 '影匯',
 '王心凌',
 '悶鍋',
 '題材',
 '綜藝',
 '明星',
 'to',
 '開賣',
 '木村拓',
 '婚禮',
 '尼克',
 '木村',
 '朴',
 '寶劍',
 '羅馬',
 '夏于喬',
 '日籍',
 '伍思凱',
 '尼可拉',
 '如懿傳',
 '周迅',
 '坎城',
 '繼',
 'KKBOX',
 '單曲',
 '葛萊美',
 '楊',
 '真正',
 '長大',
 '演',
 '喜劇類',
 '富豪',
 '公視',
 '莊豐',
 '嘉',
 '金鐘',
 '巨蛋',
 '完美'

In [2928]:
ujujuj ={}
len(ujujuj.keys()) < 2

True